In [1]:
import torch
import torch.nn as nn
from transformers import BertConfig, BertModel, AutoTokenizer
from transformers import Seq2SeqTrainer, Seq2SeqTrainingArguments, DataCollatorForSeq2Seq, EarlyStoppingCallback
from torch.utils.data import Dataset
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split

def global_ap(x):
    return torch.mean(x.view(x.size(0), x.size(1), -1), dim=1)

class SimSonEncoder(nn.Module):
    def __init__(self, config: BertConfig, max_len: int, dropout: float = 0.1):
        super(SimSonEncoder, self).__init__()
        self.config = config
        self.max_len = max_len
        self.bert = BertModel(config, add_pooling_layer=False)
        self.linear = nn.Linear(config.hidden_size, max_len)
        self.dropout = nn.Dropout(dropout)
    
    def forward(self, input_ids, attention_mask=None):
        if attention_mask is None:
            attention_mask = input_ids.ne(0)
        outputs = self.bert(input_ids=input_ids, attention_mask=attention_mask)
        hidden_states = outputs.last_hidden_state
        hidden_states = self.dropout(hidden_states)
        pooled = global_ap(hidden_states)
        out = self.linear(pooled)
        return out

class SimSonDecoder(nn.Module):
    def __init__(self, embedding_dim, hidden_dim, vocab_size, max_len):
        super(SimSonDecoder, self).__init__()
        self.embedding_dim = embedding_dim
        self.hidden_dim = hidden_dim
        self.vocab_size = vocab_size
        self.max_len = max_len
        
        # Project embedding to hidden dimension
        self.embedding_projection = nn.Linear(embedding_dim, hidden_dim)
        
        # Token embeddings for decoder input
        self.token_embeddings = nn.Embedding(vocab_size, hidden_dim)
        self.position_embeddings = nn.Embedding(max_len, hidden_dim)
        
        # Transformer decoder layers
        decoder_layer = nn.TransformerDecoderLayer(
            d_model=hidden_dim,
            nhead=12,
            dim_feedforward=2048,
            dropout=0.1,
            batch_first=True
        )
        self.transformer_decoder = nn.TransformerDecoder(decoder_layer, num_layers=6)
        
        # Output projection to vocabulary
        self.output_projection = nn.Linear(hidden_dim, vocab_size)
        self.dropout = nn.Dropout(0.1)
        
        # Layer normalization
        self.layer_norm = nn.LayerNorm(hidden_dim)
        
    def forward(self, molecule_embeddings, decoder_input_ids, decoder_attention_mask=None):
        batch_size, seq_len = decoder_input_ids.shape
        device = decoder_input_ids.device
        
        # Project molecule embeddings to memory for cross-attention
        memory = self.embedding_projection(molecule_embeddings)  # [batch, hidden_dim]
        memory = memory.unsqueeze(1)  # [batch, 1, hidden_dim]
        
        # Create decoder input embeddings
        token_emb = self.token_embeddings(decoder_input_ids)  # [batch, seq_len, hidden_dim]
        
        # Add positional embeddings
        positions = torch.arange(seq_len, device=device).unsqueeze(0).expand(batch_size, -1)
        pos_emb = self.position_embeddings(positions)
        
        decoder_inputs = self.layer_norm(token_emb + pos_emb)
        decoder_inputs = self.dropout(decoder_inputs)
        
        # Create causal mask for decoder
        tgt_mask = self._generate_square_subsequent_mask(seq_len).to(device)
        
        # Create attention mask for decoder inputs
        if decoder_attention_mask is not None:
            # Convert padding mask to additive mask
            tgt_key_padding_mask = (decoder_attention_mask == 0)
        else:
            tgt_key_padding_mask = None
        
        # Apply transformer decoder
        decoder_output = self.transformer_decoder(
            tgt=decoder_inputs,
            memory=memory,
            tgt_mask=tgt_mask,
            tgt_key_padding_mask=tgt_key_padding_mask
        )
        
        # Project to vocabulary
        logits = self.output_projection(decoder_output)
        
        return logits
    
    def _generate_square_subsequent_mask(self, sz):
        """Generate causal mask for decoder"""
        mask = torch.triu(torch.ones(sz, sz) * float('-inf'), diagonal=1)
        return mask

# Combined Encoder-Decoder Model
class SimSonEncoderDecoder(nn.Module):
    def __init__(self, encoder, decoder, tokenizer):
        super().__init__()
        self.encoder = encoder
        self.decoder = decoder
        self.tokenizer = tokenizer

    def forward(self, input_ids, attention_mask, labels=None):
        # Encode SMILES to embeddings
        embeddings = self.encoder(input_ids, attention_mask)
        
        if labels is not None:
            # During training, use teacher forcing
            # Shift labels for decoder input (remove last token, add BOS token)
            decoder_input_ids = torch.cat([
                torch.full((labels.shape[0], 1), self.tokenizer.cls_token_id, 
                          dtype=labels.dtype, device=labels.device),
                labels[:, :-1]
            ], dim=1)
            
            # Generate decoder attention mask
            decoder_attention_mask = (decoder_input_ids != self.tokenizer.pad_token_id).long()
            
            # Decode embeddings to SMILES
            logits = self.decoder(embeddings, decoder_input_ids, decoder_attention_mask)
            
            # Calculate loss
            loss_fct = nn.CrossEntropyLoss(ignore_index=self.tokenizer.pad_token_id)
            loss = loss_fct(logits.view(-1, logits.size(-1)), labels.view(-1))
            
            return {"loss": loss, "logits": logits}
        else:
            # During inference
            return self.generate(embeddings)
    
    def generate(self, embeddings, max_length=512):
        """Generate SMILES from embeddings"""
        batch_size = embeddings.shape[0]
        device = embeddings.device
        
        # Start with CLS token
        generated = torch.full((batch_size, 1), self.tokenizer.cls_token_id, 
                              dtype=torch.long, device=device)
        
        for _ in range(max_length - 1):
            decoder_attention_mask = (generated != self.tokenizer.pad_token_id).long()
            logits = self.decoder(embeddings, generated, decoder_attention_mask)
            
            # Get next token probabilities
            next_token_logits = logits[:, -1, :]
            next_tokens = torch.argmax(next_token_logits, dim=-1, keepdim=True)
            
            # Append to generated sequence
            generated = torch.cat([generated, next_tokens], dim=1)
            
            # Stop if all sequences have generated EOS token
            if torch.all(next_tokens.squeeze() == self.tokenizer.sep_token_id):
                break
                
        return generated

# Initialize tokenizer
tokenizer = AutoTokenizer.from_pretrained('DeepChem/ChemBERTa-77M-MTR')

# Initialize encoder config
config = BertConfig(
    vocab_size=tokenizer.vocab_size,
    hidden_size=768,
    num_hidden_layers=4,
    num_attention_heads=4,
    intermediate_size=2048,
    max_position_embeddings=512
)

# Initialize and load encoder
encoder = SimSonEncoder(config=config, max_len=512)

# Load encoder parameters (extract encoder from regression model)
regression_state_dict = torch.load('/home/jovyan/simson_training_bolgov/regression/better_regression_states/best_state.bin', weights_only=False)

encoder_state_dict = {}
for key, value in regression_state_dict.items():
    key = key[len('_orig_mod.'):]
    if key.startswith('encoder.'):
        encoder_state_dict[key[8 + len('_orig_mod.'):]] = value

print("Encoder parameters loaded")

# Freeze encoder parameters
for param in encoder.parameters():
    param.requires_grad = False
print("Encoder parameters frozen")

# Initialize decoder
decoder = SimSonDecoder(
    embedding_dim=512,  # encoder.max_len
    hidden_dim=768,     # config.hidden_size
    vocab_size=tokenizer.vocab_size,
    max_len=512
)

# Create combined model
model = SimSonEncoderDecoder(encoder, decoder, tokenizer)


Encoder parameters loaded
Encoder parameters frozen


regression_params = torch.load('/home/jovyan/simson_training_bolgov/regression/simson_encoder_decoder.bin', weights_only=False)

uncompiled_state_dict = {}
for key, value in regression_params.items():
    print(key)
    key = key[len('_orig_mod.'):]
    uncompiled_state_dict[key] = value
    print(key)
    break
    
torch.save(uncompiled_state_dict, '/home/jovyan/simson_training_bolgov/regression/encoder_decoder_uncompiled.bin')

In [2]:
# Load dataset
df = pd.read_csv('/home/jovyan/simson_training_bolgov/regression/PI_Tg_P308K_synth_db_chem.csv')

In [3]:
class SMILESReconstructionDataset(Dataset):
    def __init__(self, dataframe, tokenizer, max_length=256):
        self.data = dataframe
        self.tokenizer = tokenizer
        self.max_length = max_length
    
    def __len__(self):
        return len(self.data)
    
    def __getitem__(self, idx):
        # Get SMILES string (adjust column name as needed)
        smiles = self.data.iloc[idx]['smiles'] if 'smiles' in self.data.columns else self.data.iloc[idx]['Smiles']
        
        # Tokenize input SMILES
        encoding = self.tokenizer(
            smiles,
            max_length=self.max_length,
            padding='max_length',
            truncation=True,
            return_tensors='pt'
        )
        
        return {
            'input_ids': encoding['input_ids'].squeeze(0),
            'attention_mask': encoding['attention_mask'].squeeze(0),
            'labels': encoding['input_ids'].squeeze(0)  # Same as input for reconstruction
        }

def create_stratified_splits_regression(
    df,
    label_cols,
    n_bins=10,
    val_frac=0.05,
    seed=42
):
 
    values = df[label_cols].values
    # Each label gets its own bins, based on the overall distribution
    bins = [np.unique(np.quantile(values[:,i], np.linspace(0, 1, n_bins+1))) for i in range(len(label_cols))]
    # Assign each row to a bin for each label
    inds = [
        np.digitize(values[:,i], bins[i][1:-1], right=False)  # exclude leftmost/rightmost for in-bin, avoids all bin edges as bins
        for i in range(len(label_cols))
    ]
    # Combine into a single integer stratification variable (tuple or max or sum...)
    strat_col = np.maximum.reduce(inds)  # This ensures high bin in one = high bin overall
    # Use sklearn's train_test_split with stratify
    train_idx, val_idx = train_test_split(
        df.index.values,
        test_size=val_frac,
        random_state=seed,
        shuffle=True,
        stratify=strat_col
    )
    train = df.loc[train_idx].reset_index(drop=True)
    val = df.loc[val_idx].reset_index(drop=True)
    return train, val


tokenizer_path = 'DeepChem/ChemBERTa-77M-MTR'
tokenizer = AutoTokenizer.from_pretrained(tokenizer_path)

# Same splits
train, test = create_stratified_splits_regression(
    df,
    label_cols=['CO2', 'CH4'], 
    n_bins=10,
    val_frac=0.05,
    seed=42
)

train_dataset = SMILESReconstructionDataset(train, tokenizer)
val_dataset = SMILESReconstructionDataset(test, tokenizer)
val_df = test
train_df = train
print(f"Training samples: {len(train_dataset)}")
print(f"Validation samples: {len(val_dataset)}")


Training samples: 6390602
Validation samples: 336348


In [4]:
# Custom data collator for encoder-decoder
class EncoderDecoderDataCollator:
    def __init__(self, tokenizer):
        self.tokenizer = tokenizer
    
    def __call__(self, batch):
        # Stack all batch elements
        input_ids = torch.stack([item['input_ids'] for item in batch])
        attention_mask = torch.stack([item['attention_mask'] for item in batch])
        labels = torch.stack([item['labels'] for item in batch])
        
        return {
            'input_ids': input_ids,
            'attention_mask': attention_mask,
            'labels': labels
        }


data_collator = EncoderDecoderDataCollator(tokenizer)

early_stopping_callback = EarlyStoppingCallback(
    early_stopping_patience=10,
)

training_args = Seq2SeqTrainingArguments(
    output_dir='/home/jovyan/simson_training_bolgov/regression/decoder_checkpoints',
    eval_strategy='steps',
    eval_steps=10_000,
    logging_steps=10_000,
    save_steps=10_000,
    save_total_limit=3,
    learning_rate=5e-5,
    per_device_train_batch_size=256,
    per_device_eval_batch_size=256,
    gradient_accumulation_steps=1,
    num_train_epochs=5,
    warmup_steps=50,
    weight_decay=0.01,
    logging_dir='./logs',
    report_to='none',
    load_best_model_at_end=True,
    metric_for_best_model='eval_loss',
    greater_is_better=False,
    fp16=True,
    dataloader_pin_memory=True,
    remove_unused_columns=False,
    predict_with_generate=False 
)

# Initialize trainer
trainer = Seq2SeqTrainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=val_dataset,
    data_collator=data_collator,
    tokenizer=tokenizer
)


/tmp/ipykernel_330276/2978564159.py:51: FutureWarning: `tokenizer` is deprecated and will be removed in version 5.0.0 for `Seq2SeqTrainer.__init__`. Use `processing_class` instead.
  trainer = Seq2SeqTrainer(


In [ ]:
trainer.train()

In [ ]:
final_state = trainer.model.state_dict()
torch.save(final_state, '/home/jovyan/simson_training_bolgov/regression/simson_encoder_decoder_better_regression.bin')

In [5]:
import torch.nn.functional as F


def global_ap(x):
    return torch.mean(x.view(x.size(0), x.size(1), -1), dim=1)

class SimSonEncoder(nn.Module):
    def __init__(self, config: BertConfig, max_len: int, dropout: float = 0.1):
        super(SimSonEncoder, self).__init__()
        self.config = config
        self.max_len = max_len
        self.bert = BertModel(config, add_pooling_layer=False)
        self.linear = nn.Linear(config.hidden_size, max_len)
        self.dropout = nn.Dropout(dropout)
    
    def forward(self, input_ids, attention_mask=None):
        if attention_mask is None:
            attention_mask = input_ids.ne(0)
        outputs = self.bert(input_ids=input_ids, attention_mask=attention_mask)
        hidden_states = outputs.last_hidden_state
        hidden_states = self.dropout(hidden_states)
        pooled = global_ap(hidden_states)
        out = self.linear(pooled)
        return out

class SimSonDecoder(nn.Module):
    def __init__(self, embedding_dim, hidden_dim, vocab_size, max_len):
        super(SimSonDecoder, self).__init__()
        self.embedding_dim = embedding_dim
        self.hidden_dim = hidden_dim
        self.vocab_size = vocab_size
        self.max_len = max_len
        
        # Project embedding to hidden dimension
        self.embedding_projection = nn.Linear(embedding_dim, hidden_dim)
        
        # Token embeddings for decoder input
        self.token_embeddings = nn.Embedding(vocab_size, hidden_dim)
        self.position_embeddings = nn.Embedding(max_len, hidden_dim)
        
        # Transformer decoder layers
        decoder_layer = nn.TransformerDecoderLayer(
            d_model=hidden_dim,
            nhead=12,
            dim_feedforward=2048,
            dropout=0.1,
            batch_first=True
        )
        self.transformer_decoder = nn.TransformerDecoder(decoder_layer, num_layers=6)
        
        # Output projection to vocabulary
        self.output_projection = nn.Linear(hidden_dim, vocab_size)
        self.dropout = nn.Dropout(0.1)
        
        # Layer normalization
        self.layer_norm = nn.LayerNorm(hidden_dim)
        
    def forward(self, molecule_embeddings, decoder_input_ids, decoder_attention_mask=None):
        batch_size, seq_len = decoder_input_ids.shape
        device = decoder_input_ids.device
        
        # Project molecule embeddings to memory for cross-attention
        memory = self.embedding_projection(molecule_embeddings)  # [batch, hidden_dim]
        memory = memory.unsqueeze(1)  # [batch, 1, hidden_dim]
        
        # Create decoder input embeddings
        token_emb = self.token_embeddings(decoder_input_ids)  # [batch, seq_len, hidden_dim]
        
        # Add positional embeddings
        positions = torch.arange(seq_len, device=device).unsqueeze(0).expand(batch_size, -1)
        pos_emb = self.position_embeddings(positions)
        
        decoder_inputs = self.layer_norm(token_emb + pos_emb)
        decoder_inputs = self.dropout(decoder_inputs)
        
        # Create causal mask for decoder
        tgt_mask = self._generate_square_subsequent_mask(seq_len).to(device)
        
        # Create attention mask for decoder inputs
        if decoder_attention_mask is not None:
            # Convert padding mask to additive mask
            tgt_key_padding_mask = (decoder_attention_mask == 0)
        else:
            tgt_key_padding_mask = None
        
        # Apply transformer decoder
        decoder_output = self.transformer_decoder(
            tgt=decoder_inputs,
            memory=memory,
            tgt_mask=tgt_mask,
            tgt_key_padding_mask=tgt_key_padding_mask
        )
        
        # Project to vocabulary
        logits = self.output_projection(decoder_output)
        
        return logits
    
    def _generate_square_subsequent_mask(self, sz):
        """Generate causal mask for decoder"""
        mask = torch.triu(torch.ones(sz, sz) * float('-inf'), diagonal=1)
        return mask

# Combined Encoder-Decoder Model
class SimSonEncoderDecoder(nn.Module):
    def __init__(self, encoder, decoder, tokenizer):
        super().__init__()
        self.encoder = encoder
        self.decoder = decoder
        self.tokenizer = tokenizer
        
    def forward(self, input_ids, attention_mask, labels=None):
        # Encode SMILES to embeddings
        embeddings = self.encoder(input_ids, attention_mask)
        
        if labels is not None:
            # During training, use teacher forcing
            # Shift labels for decoder input (remove last token, add BOS token)
            decoder_input_ids = torch.cat([
                torch.full((labels.shape[0], 1), self.tokenizer.cls_token_id, 
                          dtype=labels.dtype, device=labels.device),
                labels[:, :-1]
            ], dim=1)
            
            # Generate decoder attention mask
            decoder_attention_mask = (decoder_input_ids != self.tokenizer.pad_token_id).long()
            
            # Decode embeddings to SMILES
            logits = self.decoder(embeddings, decoder_input_ids, decoder_attention_mask)
            
            # Calculate loss
            loss_fct = nn.CrossEntropyLoss(ignore_index=self.tokenizer.pad_token_id)
            loss = loss_fct(logits.view(-1, logits.size(-1)), labels.view(-1))
            
            return {"loss": loss, "logits": logits}
        else:
            # During inference
            return self.generate(embeddings)
    
    def generate(self, embeddings, max_length=512, temperature=1.0):

        batch_size = embeddings.shape[0]
        device = embeddings.device
        
        # Start with the CLS token for all sequences in the batch
        generated = torch.full((batch_size, 1), self.tokenizer.cls_token_id, 
                              dtype=torch.long, device=device)
        
        # --- THE FIX: Keep track of which sequences have finished ---
        # A boolean tensor, initially all False.
        is_finished = torch.zeros(batch_size, dtype=torch.bool, device=device)
    
        for _ in range(max_length - 1):
            # Pass the current generated sequences to the decoder
            decoder_attention_mask = (generated != self.tokenizer.pad_token_id).long()
            logits = self.decoder(embeddings, generated, decoder_attention_mask)
            
            # Focus on the logits for the last token in each sequence
            next_token_logits = logits[:, -1, :]
            
            # Apply temperature sampling
            if temperature == 0.0:
                next_tokens = torch.argmax(next_token_logits, dim=-1)
            else:
                probs = F.softmax(next_token_logits / temperature, dim=-1)
                next_tokens = torch.multinomial(probs, num_samples=1).squeeze(-1)
                
            # --- THE FIX: Prevent finished sequences from generating new tokens ---
            # If a sequence is already finished, its next token should be a pad token.
            # Otherwise, use the newly generated token.
            next_tokens = torch.where(is_finished, self.tokenizer.pad_token_id, next_tokens)
            
            # Append the new tokens to the generated sequences
            generated = torch.cat([generated, next_tokens.unsqueeze(-1)], dim=1)
            
            # --- THE FIX: Update the `is_finished` status for any sequence that just produced an EOS token ---
            is_finished |= (next_tokens == self.tokenizer.sep_token_id)
            
            # --- THE FIX: Stop if all sequences in the batch are finished ---
            if torch.all(is_finished):
                break
                
        return generated


# Initialize tokenizer
tokenizer = AutoTokenizer.from_pretrained('DeepChem/ChemBERTa-77M-MTR')

# Initialize encoder config
config = BertConfig(
    vocab_size=tokenizer.vocab_size,
    hidden_size=768,
    num_hidden_layers=4,
    num_attention_heads=12,
    intermediate_size=2048,
    max_position_embeddings=512
)

# Initialize and load encoder
encoder = SimSonEncoder(config=config, max_len=512)

# Initialize decoder
decoder = SimSonDecoder(
    embedding_dim=512,  # encoder.max_len
    hidden_dim=768,     # config.hidden_size
    vocab_size=tokenizer.vocab_size,
    max_len=512
)

# Create combined model
model = SimSonEncoderDecoder(encoder, decoder, tokenizer)
model.load_state_dict(torch.load('/home/jovyan/simson_training_bolgov/regression/simson_encoder_decoder.bin', weights_only=False))
model.cuda()
print(f"Model initialized with {sum(p.numel() for p in model.parameters() if p.requires_grad):,} trainable parameters")

Model initialized with 72,264,271 trainable parameters


In [6]:
import torch
import torch.nn as nn
import joblib
import numpy as np
from transformers import BertConfig, AutoTokenizer, BertModel
from tqdm import tqdm

# Load tokenizer
tokenizer = AutoTokenizer.from_pretrained('DeepChem/ChemBERTa-77M-MTR')

# Initialize model configuration
config = BertConfig(
    vocab_size=tokenizer.vocab_size,
    hidden_size=768,
    num_hidden_layers=4,
    num_attention_heads=12,
    intermediate_size=2048,
    max_position_embeddings=512
)

# Initialize regression model
def global_ap(x):
    return torch.mean(x.view(x.size(0), x.size(1), -1), dim=1)

class SimSonEncoder(nn.Module):
    def __init__(self, config: BertConfig, max_len: int, dropout: float = 0.1):
        super(SimSonEncoder, self).__init__()
        self.config = config
        self.max_len = max_len
        self.bert = BertModel(config, add_pooling_layer=False)
        self.linear = nn.Linear(config.hidden_size, max_len)
        self.dropout = nn.Dropout(dropout)
        
    def forward(self, input_ids, attention_mask=None):
        if attention_mask is None:
            attention_mask = input_ids.ne(0)
        outputs = self.bert(input_ids=input_ids, attention_mask=attention_mask)
        hidden_states = outputs.last_hidden_state
        hidden_states = self.dropout(hidden_states)
        pooled = global_ap(hidden_states)
        out = self.linear(pooled)
        return out

class SimSonClassifier(nn.Module):
    def __init__(self, encoder: SimSonEncoder, num_labels: int, dropout=0.1):
        super(SimSonClassifier, self).__init__()
        self.encoder = encoder
        self.clf = nn.Linear(encoder.max_len, num_labels)
        self.relu = nn.ReLU()
        self.dropout = nn.Dropout(dropout)

    def forward(self, input_ids, attention_mask=None, labels=None):
        x = self.encoder(input_ids, attention_mask)
        x = self.relu(self.dropout(x))
        x = self.clf(x)
        return x

compiling = False
# Load model and parameters
encoder = SimSonEncoder(config=config, max_len=512)
if compiling:
    encoder = torch.compile(encoder)
encoder_expert = SimSonEncoder(config=config, max_len=512)

regression_model = SimSonClassifier(encoder=encoder, num_labels=6)
regression_expert_model = SimSonClassifier(encoder=encoder_expert, num_labels=6)

if compiling:
    regression_model = torch.compile(regression_model)

# Load trained parameters
regression_params = torch.load('/home/jovyan/simson_training_bolgov/regression/better_regression_states/best_state.bin', weights_only=False)
regression_expert_params = torch.load('/home/jovyan/simson_training_bolgov/regression/high_regression_old_scalers_simson.pth', weights_only=False)


regression_model.load_state_dict(regression_params)
regression_expert_model.load_state_dict(regression_expert_params)

regression_model.eval()
regression_model.cuda()

regression_expert_model.eval()
regression_expert_model.cuda()

# Load scalers
scalers = joblib.load('/home/jovyan/simson_training_bolgov/regression/scalers')
scaler_ch4 = scalers[-2]  # CH4 scaler
scaler_co2 = scalers[-1]  # CO2 scaler

In [7]:
from rdkit import Chem
from rdkit.Chem import MolToSmiles
from tqdm import tqdm
import torch

def validate_reconstruction(model, tokenizer, test_smiles_list, num_samples=20, max_length=256):
    """
    Evaluate reconstruction quality.
    • exact_match ........ literal string equality
    • canonical_match .... same molecule after canonicalisation
    • generated_valid .... RDKit is able to parse generated SMILES
    """
    model.eval()
    device = next(model.parameters()).device

    results = []
    with torch.no_grad():
        for i, smiles in enumerate(test_smiles_list[:num_samples]):
            # ---------- encode ----------
            tokens = tokenizer(
                smiles,
                max_length=max_length,
                truncation=True,
                padding="max_length",
                return_tensors="pt"
            ).to(device)

            embedding = model.encoder(tokens["input_ids"], tokens["attention_mask"])

            # ---------- decode ----------
            gen_ids = model.generate(embedding)
            gen_smiles = tokenizer.decode(gen_ids[0], skip_special_tokens=True)

            # ---------- validity ----------
            mol_orig = Chem.MolFromSmiles(smiles)
            mol_gen  = Chem.MolFromSmiles(gen_smiles)
            orig_valid = mol_orig is not None
            gen_valid  = mol_gen  is not None

            # ---------- canonical comparison ----------
            if orig_valid and gen_valid:
                can_orig = MolToSmiles(mol_orig, canonical=True)
                can_gen  = MolToSmiles(mol_gen,  canonical=True)
                canonical_match = (can_orig == can_gen)
            else:
                canonical_match = False

            results.append({
                "original":          smiles,
                "reconstructed":     gen_smiles,
                "exact_match":       smiles == gen_smiles,
                "canonical_match":   canonical_match,
                "generated_valid":   gen_valid
            })

            print(f"\nSample {i+1}")
            print(f"  Original:      {smiles}")
            print(f"  Reconstructed: {gen_smiles}")
            print(f"  Valid (gen):   {gen_valid}")
            print(f"  Same molecule: {canonical_match}")
            print("-" * 60)

    # ---------- aggregated metrics ----------
    exact_acc      = sum(r["exact_match"]     for r in results) / len(results)
    canonical_acc  = sum(r["canonical_match"] for r in results) / len(results)
    validity_rate  = sum(r["generated_valid"] for r in results) / len(results)

    print(f"\nExact-string match accuracy ...... {exact_acc:.2%}")
    print(f"Canonical match accuracy ......... {canonical_acc:.2%}")
    print(f"Generated validity rate .......... {validity_rate:.2%}")

    return results

test_smiles = val_df['smiles' if 'smiles' in val_df.columns else 'Smiles'].tolist()
#validation_results = validate_reconstruction(model, tokenizer, test_smiles, num_samples=20)


In [115]:
from sklearn.metrics import pairwise_distances
from sklearn.preprocessing import MinMaxScaler


features = ['CO2', 'CH4']

# --- 3. Max–Min selection ----------------------------------------------------
def select_diverse_maxmin(data, cols, k=1_000):
    X = data[cols].to_numpy()
    
    # scale to [0,1] so CO₂ and CH₄ get equal weight
    X = MinMaxScaler().fit_transform(X)
    
    n = len(X)
    if k >= n: # nothing to do
        return data
    
    # start with a random seed point
    selected = [np.random.randint(0, n)]
    
    # pre-allocate distance cache
    min_dist = pairwise_distances(
        X, X[selected], metric='euclidean'
    ).ravel()          # distance to first point
    
    for _ in tqdm(range(1, k)):
        # pick the point with the largest distance to the current set
        idx = np.argmax(min_dist)
        selected.append(idx)
        
        # update distance cache (keep the shortest distance to any selected pt)
        dist_to_new = pairwise_distances(X, X[[idx]], metric='euclidean').ravel()
        min_dist = np.minimum(min_dist, dist_to_new)
    
    return data.iloc[selected].reset_index(drop=True)

sample_df = select_diverse_maxmin(df, features, k=1_000)

100%|█████████████████████████████████████████| 999/999 [04:08<00:00,  4.02it/s]


In [8]:
import torch
import numpy as np
import pandas as pd
from rdkit import Chem
from rdkit.Chem import MolToSmiles
from scipy.stats import pearsonr, spearmanr
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from tqdm import tqdm
import matplotlib.pyplot as plt
import seaborn as sns

def display_property_fidelity_results(results_df, metrics):
    """Display comprehensive property fidelity analysis"""
    
    valid_results = results_df[results_df['reconstructed_valid']].copy()
    total_molecules = len(results_df)
    valid_molecules = len(valid_results)
    identical_molecules = results_df['chemically_identical'].sum()
    
    print(f"\n{'='*80}")
    print(f"PROPERTY RECONSTRUCTION FIDELITY ANALYSIS")
    print(f"{'='*80}")
    
    print(f"Dataset Overview:")
    print(f"  Total molecules tested: {total_molecules}")
    print(f"  Valid reconstructions: {valid_molecules} ({valid_molecules/total_molecules*100:.1f}%)")
    print(f"  Chemically identical: {identical_molecules} ({identical_molecules/total_molecules*100:.1f}%)")
    
    if valid_molecules > 0:
        print(f"\n{'='*60}")
        print(f"PROPERTY CORRELATION METRICS")
        print(f"{'='*60}")
        
        print(f"CH₄ Permeability:")
        print(f"  Pearson correlation: {metrics['CH4']['pearson_correlation']:.4f}")
        print(f"  Spearman correlation: {metrics['CH4']['spearman_correlation']:.4f}")
        print(f"  R² score: {metrics['CH4']['r2_score']:.4f}")
        print(f"  MAE: {metrics['CH4']['mae']:.4f}")
        print(f"  RMSE: {metrics['CH4']['rmse']:.4f}")
        print(f"  Mean relative error: {metrics['CH4']['mean_relative_error_pct']:.2f}%")
        print(f"  Median relative error: {metrics['CH4']['median_relative_error_pct']:.2f}%")
        
        print(f"\nCO₂ Permeability:")
        print(f"  Pearson correlation: {metrics['CO2']['pearson_correlation']:.4f}")
        print(f"  Spearman correlation: {metrics['CO2']['spearman_correlation']:.4f}")
        print(f"  R² score: {metrics['CO2']['r2_score']:.4f}")
        print(f"  MAE: {metrics['CO2']['mae']:.4f}")
        print(f"  RMSE: {metrics['CO2']['rmse']:.4f}")
        print(f"  Mean relative error: {metrics['CO2']['mean_relative_error_pct']:.2f}%")
        print(f"  Median relative error: {metrics['CO2']['median_relative_error_pct']:.2f}%")
        
        # Property preservation quality assessment
        print(f"\n{'='*60}")
        print(f"PROPERTY PRESERVATION ASSESSMENT")
        print(f"{'='*60}")
        
        # Define quality thresholds
        excellent_threshold = 5.0  # <5% relative error
        good_threshold = 15.0      # <15% relative error
        acceptable_threshold = 30.0 # <30% relative error
        
        ch4_excellent = (valid_results['CH4_relative_error'] < excellent_threshold).sum()
        ch4_good = (valid_results['CH4_relative_error'] < good_threshold).sum()
        ch4_acceptable = (valid_results['CH4_relative_error'] < acceptable_threshold).sum()
        
        co2_excellent = (valid_results['CO2_relative_error'] < excellent_threshold).sum()
        co2_good = (valid_results['CO2_relative_error'] < good_threshold).sum()
        co2_acceptable = (valid_results['CO2_relative_error'] < acceptable_threshold).sum()
        
        print(f"CH₄ Property Preservation Quality:")
        print(f"  Excellent (<{excellent_threshold}% error): {ch4_excellent}/{valid_molecules} ({ch4_excellent/valid_molecules*100:.1f}%)")
        print(f"  Good (<{good_threshold}% error): {ch4_good}/{valid_molecules} ({ch4_good/valid_molecules*100:.1f}%)")
        print(f"  Acceptable (<{acceptable_threshold}% error): {ch4_acceptable}/{valid_molecules} ({ch4_acceptable/valid_molecules*100:.1f}%)")
        
        print(f"\nCO₂ Property Preservation Quality:")
        print(f"  Excellent (<{excellent_threshold}% error): {co2_excellent}/{valid_molecules} ({co2_excellent/valid_molecules*100:.1f}%)")
        print(f"  Good (<{good_threshold}% error): {co2_good}/{valid_molecules} ({co2_good/valid_molecules*100:.1f}%)")
        print(f"  Acceptable (<{acceptable_threshold}% error): {co2_acceptable}/{valid_molecules} ({co2_acceptable/valid_molecules*100:.1f}%)")


def evaluate_property_reconstruction_fidelity(model, regression_model, tokenizer, 
                                            scaler_ch4, scaler_co2, test_smiles_list,
                                            batch_size=16, max_length=256):
    """
    Evaluate how well reconstructed SMILES preserve chemical properties
    
    Args:
        model: Trained encoder-decoder model
        regression_model: Trained regression model for property prediction
        tokenizer: SMILES tokenizer
        scaler_ch4, scaler_co2: Property scalers
        test_smiles_list: List of original SMILES to test
        batch_size: Batch size for processing
        max_length: Maximum SMILES length
        
    Returns:
        results_df: DataFrame with detailed property comparison results
        metrics: Dictionary of aggregate evaluation metrics
    """
    
    model.eval()
    regression_model.eval()
    device = next(model.parameters()).device
    
    results = []
    
    print(f"Evaluating property reconstruction fidelity for {len(test_smiles_list)} molecules...")
    
    # Process in batches for memory efficiency
    for i in tqdm(range(0, len(test_smiles_list), batch_size), desc="Processing batches"):
        batch_end = min(i + batch_size, len(test_smiles_list))
        batch_smiles = test_smiles_list[i:batch_end]
        
        with torch.no_grad():
            # Step 1: Generate embeddings from original SMILES
            original_tokens = tokenizer(
                batch_smiles,
                max_length=max_length,
                padding='max_length',
                truncation=True,
                return_tensors='pt'
            ).to(device)
            
            # Get embeddings
            embeddings = model.encoder(original_tokens['input_ids'].cuda(), original_tokens['attention_mask'].cuda())
            
            # Step 2: Reconstruct SMILES from embeddings
            reconstructed_ids = model.generate(embeddings, temperature=1.5)
            
            # Step 3: Predict properties for both original and reconstructed
            # Original properties
            orig_predictions = regression_model(original_tokens['input_ids'], original_tokens['attention_mask'])
            orig_ch4_scaled = orig_predictions[:, -2].cpu().numpy().reshape(-1, 1)
            orig_co2_scaled = orig_predictions[:, -1].cpu().numpy().reshape(-1, 1)
            orig_ch4 = scaler_ch4.inverse_transform(orig_ch4_scaled).flatten()
            orig_co2 = scaler_co2.inverse_transform(orig_co2_scaled).flatten()
            
            # Reconstructed properties
            reconstructed_smiles = [tokenizer.decode(seq, skip_special_tokens=True) for seq in reconstructed_ids]
            # Validate reconstructed SMILES and predict properties
            for j, (orig_smiles, recon_smiles) in enumerate(zip(batch_smiles, reconstructed_smiles)):
                # Chemical validity checks
                orig_mol = Chem.MolFromSmiles(orig_smiles)
                recon_mol = Chem.MolFromSmiles(recon_smiles)
                
                orig_valid = orig_mol is not None
                recon_valid = recon_mol is not None
                
                # Canonical SMILES comparison
                if orig_valid and recon_valid:
                    orig_canonical = MolToSmiles(orig_mol, canonical=True)
                    recon_canonical = MolToSmiles(recon_mol, canonical=True)
                    is_identical = orig_canonical == recon_canonical
                else:
                    orig_canonical = "INVALID" if not orig_valid else MolToSmiles(orig_mol, canonical=True)
                    recon_canonical = "INVALID" if not recon_valid else MolToSmiles(recon_mol, canonical=True)
                    is_identical = False
                
                # Property prediction for reconstructed SMILES
                if recon_valid:
                    recon_tokens = tokenizer(
                        recon_smiles,
                        max_length=max_length,
                        padding='max_length',
                        truncation=True,
                        return_tensors='pt'
                    ).to(device)
                    
                    recon_predictions = regression_model(recon_tokens['input_ids'], recon_tokens['attention_mask'])
                    recon_ch4_scaled = recon_predictions[0, -2].cpu().numpy().reshape(-1, 1)
                    recon_co2_scaled = recon_predictions[0, -1].cpu().numpy().reshape(-1, 1)
                    recon_ch4 = scaler_ch4.inverse_transform(recon_ch4_scaled)[0, 0]
                    recon_co2 = scaler_co2.inverse_transform(recon_co2_scaled)[0, 0]
                else:
                    recon_ch4 = np.nan
                    recon_co2 = np.nan
                
                # Calculate property differences
                ch4_absolute_error = abs(orig_ch4[j] - recon_ch4) if recon_valid else np.nan
                co2_absolute_error = abs(orig_co2[j] - recon_co2) if recon_valid else np.nan
                
                ch4_relative_error = (ch4_absolute_error / orig_ch4[j] * 100) if (recon_valid and orig_ch4[j] != 0) else np.nan
                co2_relative_error = (co2_absolute_error / orig_co2[j] * 100) if (recon_valid and orig_co2[j] != 0) else np.nan
                
                results.append({
                    'molecule_id': i + j + 1,
                    'original_smiles': orig_smiles,
                    'reconstructed_smiles': recon_smiles,
                    'original_canonical': orig_canonical,
                    'reconstructed_canonical': recon_canonical,
                    'chemically_identical': is_identical,
                    'original_valid': orig_valid,
                    'reconstructed_valid': recon_valid,
                    'original_CH4': orig_ch4[j],
                    'original_CO2': orig_co2[j],
                    'reconstructed_CH4': recon_ch4,
                    'reconstructed_CO2': recon_co2,
                    'CH4_absolute_error': ch4_absolute_error,
                    'CO2_absolute_error': co2_absolute_error,
                    'CH4_relative_error': ch4_relative_error,
                    'CO2_relative_error': co2_relative_error
                })
    
    # Convert to DataFrame
    results_df = pd.DataFrame(results)
    
    # Calculate aggregate metrics
    valid_comparisons = results_df[results_df['reconstructed_valid']].copy()
    
    if len(valid_comparisons) > 0:
        metrics = calculate_property_fidelity_metrics(valid_comparisons)
        display_property_fidelity_results(results_df, metrics)
    else:
        print("No valid reconstructions for property comparison!")
        metrics = {}
    
    return results_df, metrics

def visualize_property_fidelity(results_df, save_plots=True):
    """Create comprehensive visualizations of property reconstruction fidelity"""
    
    valid_results = results_df[results_df['reconstructed_valid']].copy()
    
    if len(valid_results) == 0:
        print("No valid results to visualize!")
        return
    
    fig, axes = plt.subplots(2, 3, figsize=(18, 12))
    
    # 1. CH4 Property Correlation
    axes[0, 0].scatter(valid_results['original_CH4'], valid_results['reconstructed_CH4'], 
                      alpha=0.6, s=30, edgecolors='black', linewidth=0.5)
    
    # Perfect correlation line
    min_ch4 = min(valid_results['original_CH4'].min(), valid_results['reconstructed_CH4'].min())
    max_ch4 = max(valid_results['original_CH4'].max(), valid_results['reconstructed_CH4'].max())
    axes[0, 0].plot([min_ch4, max_ch4], [min_ch4, max_ch4], 'r--', linewidth=2, label='Perfect Correlation')
    
    # Calculate and display R²
    ch4_r2 = r2_score(valid_results['original_CH4'], valid_results['reconstructed_CH4'])
    axes[0, 0].set_xlabel('Original CH₄ Permeability')
    axes[0, 0].set_ylabel('Reconstructed CH₄ Permeability')
    axes[0, 0].set_title(f'CH₄ Property Reconstruction (R² = {ch4_r2:.3f})')
    axes[0, 0].legend()
    axes[0, 0].grid(True, alpha=0.3)
    
    # 2. CO2 Property Correlation
    axes[0, 1].scatter(valid_results['original_CO2'], valid_results['reconstructed_CO2'], 
                      alpha=0.6, s=30, edgecolors='black', linewidth=0.5)
    
    min_co2 = min(valid_results['original_CO2'].min(), valid_results['reconstructed_CO2'].min())
    max_co2 = max(valid_results['original_CO2'].max(), valid_results['reconstructed_CO2'].max())
    axes[0, 1].plot([min_co2, max_co2], [min_co2, max_co2], 'r--', linewidth=2, label='Perfect Correlation')
    
    co2_r2 = r2_score(valid_results['original_CO2'], valid_results['reconstructed_CO2'])
    axes[0, 1].set_xlabel('Original CO₂ Permeability')
    axes[0, 1].set_ylabel('Reconstructed CO₂ Permeability')
    axes[0, 1].set_title(f'CO₂ Property Reconstruction (R² = {co2_r2:.3f})')
    axes[0, 1].legend()
    axes[0, 1].grid(True, alpha=0.3)
    
    # 3. Relative Error Distribution - CH4
    axes[0, 2].hist(valid_results['CH4_relative_error'].dropna(), bins=30, alpha=0.7, 
                   edgecolor='black', color='skyblue')
    axes[0, 2].axvline(valid_results['CH4_relative_error'].median(), color='red', 
                      linestyle='--', linewidth=2, label=f'Median: {valid_results["CH4_relative_error"].median():.1f}%')
    axes[0, 2].set_xlabel('CH₄ Relative Error (%)')
    axes[0, 2].set_ylabel('Frequency')
    axes[0, 2].set_title('CH₄ Relative Error Distribution')
    axes[0, 2].legend()
    axes[0, 2].grid(True, alpha=0.3)
    
    # 4. Relative Error Distribution - CO2
    axes[1, 0].hist(valid_results['CO2_relative_error'].dropna(), bins=30, alpha=0.7, 
                   edgecolor='black', color='lightcoral')
    axes[1, 0].axvline(valid_results['CO2_relative_error'].median(), color='red', 
                      linestyle='--', linewidth=2, label=f'Median: {valid_results["CO2_relative_error"].median():.1f}%')
    axes[1, 0].set_xlabel('CO₂ Relative Error (%)')
    axes[1, 0].set_ylabel('Frequency')
    axes[1, 0].set_title('CO₂ Relative Error Distribution')
    axes[1, 0].legend()
    axes[1, 0].grid(True, alpha=0.3)
    
    # 5. Error Comparison
    error_comparison = pd.DataFrame({
        'CH₄_Error': valid_results['CH4_relative_error'].dropna(),
        'CO₂_Error': valid_results['CO2_relative_error'].dropna()
    })
    
    axes[1, 1].scatter(error_comparison['CH₄_Error'], error_comparison['CO₂_Error'], 
                      alpha=0.6, s=30, edgecolors='black', linewidth=0.5)
    axes[1, 1].set_xlabel('CH₄ Relative Error (%)')
    axes[1, 1].set_ylabel('CO₂ Relative Error (%)')
    axes[1, 1].set_title('Property Error Correlation')
    axes[1, 1].grid(True, alpha=0.3)
    
    # 6. Chemical Identity vs Property Preservation
    identical_mask = valid_results['chemically_identical']
    
    ch4_errors_identical = valid_results[identical_mask]['CH4_relative_error'].dropna()
    ch4_errors_different = valid_results[~identical_mask]['CH4_relative_error'].dropna()
    
    axes[1, 2].boxplot([ch4_errors_identical, ch4_errors_different], 
                      labels=['Chemically Identical', 'Chemically Different'])
    axes[1, 2].set_ylabel('CH₄ Relative Error (%)')
    axes[1, 2].set_title('Property Error by Chemical Identity')
    axes[1, 2].grid(True, alpha=0.3)
    
    plt.tight_layout()
    
    if save_plots:
        plt.savefig('property_reconstruction_fidelity.png', dpi=300, bbox_inches='tight')
        print("Visualization saved as 'property_reconstruction_fidelity.png'")
    
    plt.show()


def calculate_property_fidelity_metrics(valid_results):
    """Calculate comprehensive property fidelity metrics"""
    
    metrics = {}
    
    # Correlation metrics
    ch4_corr_pearson, ch4_p_pearson = pearsonr(valid_results['original_CH4'], valid_results['reconstructed_CH4'])
    co2_corr_pearson, co2_p_pearson = pearsonr(valid_results['original_CO2'], valid_results['reconstructed_CO2'])
    
    ch4_corr_spearman, ch4_p_spearman = spearmanr(valid_results['original_CH4'], valid_results['reconstructed_CH4'])
    co2_corr_spearman, co2_p_spearman = spearmanr(valid_results['original_CO2'], valid_results['reconstructed_CO2'])
    
    # Regression metrics
    ch4_r2 = r2_score(valid_results['original_CH4'], valid_results['reconstructed_CH4'])
    co2_r2 = r2_score(valid_results['original_CO2'], valid_results['reconstructed_CO2'])
    
    ch4_mae = mean_absolute_error(valid_results['original_CH4'], valid_results['reconstructed_CH4'])
    co2_mae = mean_absolute_error(valid_results['original_CO2'], valid_results['reconstructed_CO2'])
    
    ch4_rmse = np.sqrt(mean_squared_error(valid_results['original_CH4'], valid_results['reconstructed_CH4']))
    co2_rmse = np.sqrt(mean_squared_error(valid_results['original_CO2'], valid_results['reconstructed_CO2']))
    
    # Relative error statistics
    ch4_mean_rel_error = valid_results['CH4_relative_error'].mean()
    co2_mean_rel_error = valid_results['CO2_relative_error'].mean()
    
    ch4_median_rel_error = valid_results['CH4_relative_error'].median()
    co2_median_rel_error = valid_results['CO2_relative_error'].median()
    
    metrics = {
        'CH4': {
            'pearson_correlation': ch4_corr_pearson,
            'spearman_correlation': ch4_corr_spearman,
            'r2_score': ch4_r2,
            'mae': ch4_mae,
            'rmse': ch4_rmse,
            'mean_relative_error_pct': ch4_mean_rel_error,
            'median_relative_error_pct': ch4_median_rel_error
        },
        'CO2': {
            'pearson_correlation': co2_corr_pearson,
            'spearman_correlation': co2_corr_spearman,
            'r2_score': co2_r2,
            'mae': co2_mae,
            'rmse': co2_rmse,
            'mean_relative_error_pct': co2_mean_rel_error,
            'median_relative_error_pct': co2_median_rel_error
        }
    }
    
    return metrics


In [9]:
from rdkit import RDLogger

# Disable all RDKit logs
RDLogger.DisableLog('rdApp.*') 

In [26]:
df.sort_values(by=['CO2'], ascending=False)

Unnamed: 0                                             Smiles  \
5117051     5117051  Ic1ccc(nc1)C(C(F)(F)F)(C(F)(F)F)c1ccc(nc1)C(C(...   
1654268     1654268  Ic1ccc(nc1)C(C(F)(F)F)(C(F)(F)F)c1ccc(cn1)C(C(...   
6692275     6692275  Ic1ccc(cn1)C(C(F)(F)F)(C(F)(F)F)c1ccc(cn1)C(C(...   
830270       830270  Ic1ccc(nc1)C(C(F)(F)F)(C(F)(F)F)c1ccc(nc1)C(C(...   
6692276     6692276  Ic1ccc(nc1)C(C(F)(F)F)(C(F)(F)F)c1ccc(nc1)C(C(...   
...             ...                                                ...   
10950         10950  Ic1cc(Oc2cc(Oc3cc(cc(c3)n3c(=O)c4c(c3=O)cc3c(c...   
5309014     5309014  Ic1cc(cc(c1)C(=O)O)C(=O)c1cc(cc(c1)C(=O)O)C(=O...   
2598418     2598418  Ic1cc(cc(c1)C(=O)O)C(=O)c1cc(cc(c1)C(=O)O)C(=O...   
746918       746918  Ic1cc(cc(c1)C(=O)O)C(=O)c1cc(cc(c1)C(=O)O)C(=O...   
2255           2255  Ic1cc(cc(c1)C(=O)O)C(=O)c1cc(cc(c1)C(=O)O)C(=O...   

             Tg         He          N2           O2        CH4           CO2  \
5117051  544.42  343.89398  3284.48720  18341.89400  528.13604  161379.46000   
1654268  544.42  343.89398  3284.48720  18341.89400  528.13604  161379.46000   
6692275  544.42  343.89398  3284.48720  18341.89400  528.13604  161379.46000   
830270   544.42  343.89398  3284.48720  18341.89400  528.13604  161379.46000   
6692276  544.42  343.89398  3284.48720  18341.89400  528.13604  161379.46000   
...         ...        ...         ...          ...        ...           ...   
10950    538.15    1.23546     0.00105      0.00404    0.00195       0.00785   
5309014  552.00    2.56385     0.00138      0.00777    0.00287       0.00772   
2598418  552.00    2.56385     0.00138      0.00777    0.00287       0.00772   
746918   552.00    2.56385     0.00138      0.00777    0.00287       0.00772   
2255     586.80    1.80544     0.00068      0.00330    0.00184       0.00419   

         synthesizable  
5117051          False  
1654268          False  
6692275          False  
830270           False  
6692276          False  
...                ...  
10950             True  
5309014          False  
2598418          False  
746918           False  
2255             False  

[6726950 rows x 9 columns]

In [56]:
enc_gen = model.encoder.state_dict()
enc_reg = regression_model.encoder.state_dict()



In [89]:
test_smiles = sample_df['Smiles'].tolist()
test_smiles = df.sort_values(by=['CO2'], ascending=False)['Smiles'].tolist()[:100]


results_df, metrics = evaluate_property_reconstruction_fidelity(
        model=model, 
        regression_model=regression_expert_model,
        tokenizer=tokenizer,
        scaler_ch4=scaler_ch4,
        scaler_co2=scaler_co2,
        test_smiles_list=test_smiles[:1_000],
        batch_size=128
    )

Evaluating property reconstruction fidelity for 100 molecules...


Processing batches: 100%|█████████████████████████| 1/1 [00:16<00:00, 16.36s/it]


PROPERTY RECONSTRUCTION FIDELITY ANALYSIS
Dataset Overview:
  Total molecules tested: 100
  Valid reconstructions: 93 (93.0%)
  Chemically identical: 0 (0.0%)

PROPERTY CORRELATION METRICS
CH₄ Permeability:
  Pearson correlation: 0.0400
  Spearman correlation: -0.0705
  R² score: -3.0056
  MAE: 82.2622
  RMSE: 103.3733
  Mean relative error: 19.19%
  Median relative error: 24.48%

CO₂ Permeability:
  Pearson correlation: -0.1054
  Spearman correlation: -0.3209
  R² score: -3.9737
  MAE: 26978.8016
  RMSE: 33540.0662
  Mean relative error: 20.97%
  Median relative error: 26.74%

PROPERTY PRESERVATION ASSESSMENT
CH₄ Property Preservation Quality:
  Excellent (<5.0% error): 32/93 (34.4%)
  Good (<15.0% error): 33/93 (35.5%)
  Acceptable (<30.0% error): 76/93 (81.7%)

CO₂ Property Preservation Quality:
  Excellent (<5.0% error): 28/93 (30.1%)
  Good (<15.0% error): 33/93 (35.5%)
  Acceptable (<30.0% error): 57/93 (61.3%)


In [10]:
import torch
import numpy as np
from tqdm import tqdm
from rdkit import Chem
from rdkit.Chem import MolToSmiles

def generate_base_embeddings(model, tokenizer, val_df, max_length=256, batch_size=128):
    """
    Generate embeddings for molecules in validation dataset using batch processing
    
    Args:
        model: Trained encoder-decoder model
        tokenizer: SMILES tokenizer
        val_df: Validation dataframe containing SMILES
        max_length: Maximum SMILES sequence length 
        batch_size: Number of molecules to process in each batch
        
    Returns:
        base_embeddings: Tensor of shape [num_molecules, embedding_dim]
    """
    model.eval()
    device = next(model.parameters()).device
    
    smiles_list = val_df['Smiles'].tolist()
    embeddings_list = []
    
    with torch.no_grad():
        for i in tqdm(range(0, len(smiles_list), batch_size), desc="Generating base embeddings in batches"):
            # Get current batch of SMILES
            batch_end = min(i + batch_size, len(smiles_list))
            batch_smiles = smiles_list[i:batch_end]
            
            # Tokenize entire batch at once
            encoding = tokenizer(
                batch_smiles,
                max_length=max_length,
                padding='max_length',
                truncation=True,
                return_tensors='pt'
            ).to(device)
            
            with torch.autocast(dtype=torch.float16, device_type='cuda'):
                embedding_batch = model.encoder(encoding['input_ids'], encoding['attention_mask'])
            
            # Move to CPU and store
            embeddings_list.append(embedding_batch.cpu().numpy())
    
    # Stack all batch embeddings into single array
    base_embeddings = np.vstack(embeddings_list)
    
    return torch.tensor(base_embeddings, dtype=torch.float32)

In [ ]:
# Generate base embeddings
print("Generating 'base' embeddings")
base_embeddings_s = generate_base_embeddings(regression_model, tokenizer, df[:100])
print(f"Generated embeddings shape: {base_embeddings.shape}")


In [39]:
a = regression_model.encoder
b = model.encoder
a == b

False

In [68]:
import joblib

joblib.dump(base_embeddings, '/home/jovyan/simson_training_bolgov/regression/base_embeddings_new_reg.pickle')

['/home/jovyan/simson_training_bolgov/regression/base_embeddings_new_reg.pickle']

In [11]:
import joblib

base_embeddings = joblib.load('/home/jovyan/simson_training_bolgov/regression/sample_embeddings.pickle')
#expert_embeddings = joblib.load('/home/jovyan/simson_training_bolgov/regression/expert_embeddings.pickle')

In [76]:
actual_encoder = model.encoder.state_dict()
torch.save(actual_encoder, '/home/jovyan/simson_training_bolgov/regression/actual_encoder_state.pkl')

In [12]:
training_smiles_set = set(df['Smiles'].tolist())

def is_valid_polymer(smiles: str) -> bool:
    """
    Checks if a SMILES string represents a valid polymer according to specific rules.

    A valid polymer must:
    1. Be a chemically valid molecule parsable by RDKit.
    2. Contain exactly two 'I' atoms, representing polymer endpoints.
    3. Have identical bond types connecting to both endpoints.
    """
    if not isinstance(smiles, str):
        return False

    # Rule 1: Basic chemical validity
    mol = Chem.MolFromSmiles(smiles)
    if mol is None:
        return False

    # Rule 2: Must contain exactly two endpoints
    if smiles.count('I') != 2:
        return False

    # Rule 3: Endpoint bonds must match
    try:
        # Replace 'I' with a standard dummy atom '[*]' for analysis
        mol_with_dummy = Chem.MolFromSmiles(smiles.replace('I', '[*]'))
        if mol_with_dummy is None:
            return False

        # Find the atoms connected to the dummy endpoints
        matches = mol_with_dummy.GetSubstructMatches(Chem.MolFromSmarts('[#0]~*'))

        if len(matches) != 2:
            return False

        # Get the bonds connecting to the endpoints
        bond1 = mol_with_dummy.GetBondBetweenAtoms(matches[0][0], matches[0][1])
        bond2 = mol_with_dummy.GetBondBetweenAtoms(matches[1][0], matches[1][1])

        if bond1 is None or bond2 is None:
            return False

        # Check if the bond types are identical
        if bond1.GetBondType() != bond2.GetBondType():
            return False
    except Exception:
        # Catch any RDKit parsing or processing errors
        return False

    return True

def is_novel_and_valid_polymer(smiles: str, training_set: set) -> bool:
    """
    Performs a final check to ensure a molecule is both novel and a valid polymer.
    """
    # Check 1: Is it new?
    if smiles in training_set:
        print('NOT NEW')
        return False
    
    # Check 2: Does it meet polymer criteria?
    return is_valid_polymer(smiles)

In [20]:
df

Unnamed: 0                                             Smiles  \
0                 0  Ic1ccc(nc1)Cc1cccc(c1)Cc1ccc(cn1)N1C(=O)c2c(C1...   
1                 1  Ic1ccc(nc1)Cc1ccc2c(c1)cc(cc2)Cc1ccc(cn1)N1C(=...   
2                 2  O=C1c2cc(ccc2C(=O)N1c1ccc(c(c1Cl)Cl)S(=O)(=O)c...   
3                 3  Ic1cc(cc(c1)C(=O)O)C(=O)c1ccc2c(c1)ccc(c2)C(=O...   
4                 4  Clc1cc(cc(c1)C(C(F)(F)F)(C(F)(F)F)c1c(C)cc(cc1...   
...             ...                                                ...   
6726945     6726945  Ic1cccc(c1)Cc1cc(C)c(c(c1)C)c1c(C)cc(cc1C)Cc1c...   
6726946     6726946  Ic1ccc(nc1)Cc1ccc2c(c1)c1cc(ccc1C2(C)C)Cc1ccc(...   
6726947     6726947  Ic1ccc(cn1)S(=O)(=O)c1ccc(nc1)N1C(=O)c2c(C1=O)...   
6726948     6726948  Ic1ccc(c(c1)C)Oc1ccc2c(c1)Cc1c2ccc(c1)Oc1ccc(c...   
6726949     6726949  Ic1cc(Sc2ccc3c(c2)cc(cc3)Sc2cc(cc(c2)C(F)(F)F)...   

             Tg         He        N2         O2      CH4        CO2  \
0        494.84    2.69524   4.75740   42.31847  1.64086  148.43644   
1        508.26    5.33815   2.97239   26.31118  0.86467   82.37635   
2        640.91   20.47515   0.06353    0.90498  0.06905    2.35993   
3        568.04    4.19692   0.00191    0.01134  0.00362    0.01418   
4        548.10  142.68327   0.87380    8.25409  2.52067   30.04739   
...         ...        ...       ...        ...      ...        ...   
6726945  516.27   13.32967   0.11907    1.10144  0.16907    2.63642   
6726946  510.72    8.96454   7.92257   72.92929  2.17324  247.14446   
6726947  610.24    4.90758  20.24364  121.24494  1.01011  650.18364   
6726948  510.90   12.40907   0.19307    1.41335  0.11728    4.00573   
6726949  462.31   14.96342   0.13916    1.05252  0.09298    2.54411   

         synthesizable  
0                False  
1                False  
2                False  
3                False  
4                False  
...                ...  
6726945          False  
6726946          False  
6726947          False  
6726948           True  
6726949          False  

[6726950 rows x 9 columns]

In [13]:
def pred_from_embeds(embeds, regression_model):
    
    x = regression_model.relu(embeds)
    return regression_model.clf(x)

def gradient_based_extrapolation(
    generative_model, regression_model, regression_expert_model, embeddings, scaler, target_idx=-2,
    learning_rate=0.0001, steps=50, batch_size=32, best_idx=None, lambda_reg=0.3, scale_factor=1000, expert_threshold=120_000
):
    """
    Use property gradients to guide extrapolation, with checks for novelty and polymer validity.
    If an invalid or non-novel molecule is generated, optimization stops.
    """
    device = next(regression_model.parameters()).device

    # --- Freeze models to prevent parameter updates ---
    for param in regression_model.parameters():
        param.requires_grad = False
    regression_model.eval()

    for param in regression_expert_model.parameters():
        param.requires_grad = False
    regression_expert_model.eval()
    
    for param in generative_model.parameters():
        param.requires_grad = False
    generative_model.eval()

    # --- 1. Find the best starting embedding (batched) ---
    if best_idx is None:
        properties = []
        with torch.no_grad():
            for i in tqdm(range(0, len(embeddings), batch_size), desc="Computing initial properties"):
                batch = embeddings[i:i+batch_size]
                preds = regression_model.clf(batch)
                properties.append(preds[:, target_idx].cpu())
        properties = torch.cat(properties)
        best_idx = torch.argmax(properties)

    start_embedding = embeddings[best_idx].cuda().reshape(1, -1).requires_grad_(True)
    initial_embedding = start_embedding.clone().cuda()
    # This will store the last embedding that successfully passed all checks
    last_valid_embedding = start_embedding.clone().detach()

    # --- ADDITION: Store initial prediction for MAE calculation ---
    with torch.no_grad():
        initial_pred_scaled = pred_from_embeds(initial_embedding, regression_model)[:, target_idx]
        initial_pred_unscaled = initial_pred_scaled * torch.tensor(scaler.scale_, device=device) + torch.tensor(scaler.mean_, device=device)
        initial_prediction_value = initial_pred_unscaled.item()

    optimizer = torch.optim.Adam([start_embedding], lr=learning_rate)

    # --- Extract scaler attributes for PyTorch-based inverse transform ---
    scale = torch.tensor(scaler.scale_, device=device, dtype=torch.float32)
    mean = torch.tensor(scaler.mean_, device=device, dtype=torch.float32)
    # --- 2. Run gradient ascent with step-by-step checks ---
    predicting_model = regression_expert_model
    pred_unscaled = 0

    with torch.no_grad():
        pred = pred_from_embeds(start_embedding.cuda(), regression_model)
        sample_scaled = pred[:, target_idx]
        sample_unscaled = sample_scaled * scale + mean
        print(f'FIRST PRED: {sample_unscaled.detach().item()}') 

    for step in range(steps):
        if pred_unscaled >= expert_threshold:
            predicting_model = regression_expert_model
        else:
            predicting_model = regression_expert_model
    
        optimizer.zero_grad()

        pred_scaled = pred_from_embeds(start_embedding.cuda(), regression_model)[:, target_idx]
        pred_unscaled = pred_scaled * scale + mean
        property_loss = -pred_unscaled.mean()
        regularization_loss = torch.norm(start_embedding - initial_embedding, p=2)**2
        loss = property_loss + scale_factor * (lambda_reg * regularization_loss)
        
        loss.backward()
        optimizer.step()

        with torch.no_grad():
            start_embedding.clamp_(-20, 20)

        # --- VALIDATION BLOCK: Check molecule after each step ---
        with torch.no_grad():
            reconstructed_ids = generative_model.generate(start_embedding.cuda(), temperature=1.7)
            reconstructed_smiles = generative_model.tokenizer.decode(reconstructed_ids[0], skip_special_tokens=True)
            
            # Use the combined helper function for all checks
            is_valid_and_novel = is_novel_and_valid_polymer(reconstructed_smiles, training_smiles_set)
        
        print(f"Step {step+1}/{steps} | Value: {pred_unscaled.item():.4f} | SMILES: {reconstructed_smiles} | Novel & Valid Polymer: {is_valid_and_novel}")

        if is_valid_and_novel:
            # Tokenize the reconstructed SMILES
            recon_tokens = generative_model.tokenizer(
                reconstructed_smiles,
                max_length=512,
                padding='max_length',
                truncation=True,
                return_tensors='pt'
            ).to(device)
            
            # Get embedding from the reconstructed SMILES
            recon_embedding = generative_model.encoder(recon_tokens['input_ids'], recon_tokens['attention_mask'])
            
            CO2_scaled = pred_from_embeds(recon_embedding, predicting_model)[:, target_idx]
            CO2_unscaled = CO2_scaled * scale + mean
            
            print(f"  -> Reconstructed molecule CO2 permeability: {CO2_unscaled.item():.4f}")
            
            # --- ADDITION 2: Calculate MAE between initial and reconstructed prediction ---
            mae_value = float(abs(CO2_unscaled + property_loss))
            print(f"  -> MAE between initial embedding prediction and current prediction: {mae_value:.4f}")
                

            # If it passes all checks, save this as the current best state
            last_valid_embedding = start_embedding.clone().detach()
        else:
            pass

    print(f'FINAL VALUE: {pred_unscaled.detach().item():.4f}')
    return last_valid_embedding


In [14]:
sorted_df = df.sort_values(by=['CO2'], ascending=False)
best_idx = sorted_df.index.tolist()[0]
best_co2 = float(sorted_df['CO2'][best_idx])
best_embedding = base_embeddings[best_idx, :].reshape(1, -1).cuda()
best_co2, best_idx

(161379.46, 5117051)

In [ ]:
optimized_embedding = gradient_based_extrapolation(
    model, regression_model, regression_model, base_embeddings, scaler_co2, target_idx=-1, learning_rate=1e-2, steps=30, batch_size=32, best_idx=500, lambda_reg=1, scale_factor=0, expert_threshold=100_000
)

In [ ]:
example_novel_polymer = 'Ic1ccc(nc1)C(C(F)(F)F)(C(F)(F)F)c1ccc(nc1)C(C(F)(F)F)(C(F)(F)F)c1ccc(nc1)N1C(=O)c2c(C1=O)c(ccc2)C(C(F)(F)F)(C(F)(F)F)c1ccc(cn1)C(C(F)(F)F)(C(F)(F)F)c1ccc2c(c1)C(=O)N(C2=O)I'

In [58]:
df_robson = sample_df.copy()

In [4]:
!cp -r polygnn_kit/polygnn_kit .

In [79]:
!cd polygnn_kit && ls

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


'GT Open Source General Use License.pdf'   polygnn_kit.py   tests
 __init__.py				   __pycache__	    utils.py
 poetry.lock				   pyproject.toml
 polygnn_kit				   README.md


In [81]:
!rm -rf polygnn_kit/polygnn_kit

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


In [15]:
import joblib
import json

with open('polygnn/trained_models/solubility_and_permeability/metadata/selectors.json', 'r') as file:
    a = json.load(file)
    selectors = a['exp_perm_CO2__Barrer'][0]

with open('polygnn/trained_models/solubility_and_permeability/metadata/scalers.json', 'r') as file:
    scalers = json.load(file)
    polygnn_scaler = scalers['exp_perm_CO2__Barrer']

scalers

{'exp_perm_CH4__Barrer': 'Forward(MinMaxScaler(dim: 0, max: 4.07918119430542, min: -3.387216091156006))',
 'exp_perm_CO2__Barrer': 'Forward(MinMaxScaler(dim: 0, max: 4.645422458648682, min: -5.92081880569458))',
 'exp_perm_H2__Barrer': 'Forward(MinMaxScaler(dim: 0, max: 4.22788667678833, min: -1.642065167427063))',
 'exp_perm_He__Barrer': 'Forward(MinMaxScaler(dim: 0, max: 3.8041393756866455, min: -1.2612193822860718))',
 'exp_perm_N2__Barrer': 'Forward(MinMaxScaler(dim: 0, max: 3.7075700759887695, min: -3.795880079269409))',
 'exp_perm_O2__Barrer': 'Forward(MinMaxScaler(dim: 0, max: 3.931457757949829, min: -6.15490198135376))',
 'exp_solubility__MPa**0.5': 'Forward(MinMaxScaler(dim: 0, max: 29.200000762939453, min: 12.300000190734863))'}

In [17]:
root_dir = 'polygnn/trained_models/solubility_and_permeability'

In [71]:
import torch
import pandas as pd
import polygnn
import polygnn_trainer as pt
from tqdm import tqdm
import joblib
import os

def inverse_minmax(scaled_tensor,
                   min_val=-5.92081880569458,
                   max_val= 4.645422458648682):

    return scaled_tensor * (max_val - min_val) + min_val

def load_polygnn_model(model_path, device='cuda'):
    """
    Load a pre-trained polyGNN model and its configuration dynamically 
    from pickled files in the metadata folder.
    
    Args:
        model_path (str): Path to the saved model directory.
        device (str): Device to load the model on ('cuda' or 'cpu').
    
    Returns:
        tuple: Loaded ensemble model, SMILES featurizer, and the model path.
    """
    metadata_path = os.path.join(model_path, "metadata")
    if not os.path.exists(metadata_path):
        raise FileNotFoundError(f"Metadata folder not found at {metadata_path}")


    
    bond_config = polygnn.featurize.BondConfig(True, True, True)
    atom_config = polygnn.featurize.AtomConfig(
        True,
        True,
        True,
        True,
        True,
        True,
        combo_hybrid=False,
        aromatic=True,
    )
    
    ensemble = pt.load.load_ensemble(
        model_path,
        polygnn.models.polyGNN,
        device,
        submodel_kwargs_dict={
            "node_size": atom_config.n_features,
            "edge_size": bond_config.n_features,
            "selector_dim": len(selectors),
        },
        
    )
    
    # --- 5. Create the SMILES featurizer with loaded configs ---
    import functools
    kwargs = dict(bond_config=bond_config,
                  atom_config=atom_config,
                  representation="trimer")
    smiles_featurizer = functools.partial(polygnn.featurize.get_minimum_graph_tensor, **kwargs)
    
    print("polyGNN model and configuration loaded successfully from pickle files.")
    return ensemble, smiles_featurizer, model_path


def predict_co2_permeability_polygnn(smiles_list, ensemble, smiles_featurizer, model_path, device='cuda'):
    """
    Predict CO2 permeability using polyGNN model
    
    Args:
        smiles_list: List of SMILES strings
        ensemble: Loaded polyGNN ensemble model
        smiles_featurizer: SMILES featurization function
        model_path: Path to model directory (for loading scalers)
        device: Device for computation
    
    Returns:
        Tensor of CO2 permeability predictions
    """
    # Create a temporary dataframe for prediction
    temp_df = pd.DataFrame({
        'smiles_string': smiles_list,
        'prop': ['exp_perm_CO2__Barrer'] * len(smiles_list),  # Adjust property name as needed
    })
    
    # Run predictions
    with torch.no_grad():
        y, y_mean_hat, y_std_hat, _selectors = pt.infer.eval_ensemble(
            model=ensemble,
            root_dir=model_path,
            dataframe=temp_df,
            smiles_featurizer=smiles_featurizer,
            device=device,
            ensemble_kwargs_dict={"monte_carlo": False},
        )
    return y, y_mean_hat, y_std_hat

def pred_from_embeds(embeds, regression_model):
    x = regression_model.relu(embeds)
    return regression_model.clf(x)

def gradient_based_extrapolation(
    generative_model, regression_model, regression_expert_model, embeddings, scaler, target_idx=-2,
    learning_rate=0.0001, steps=50, batch_size=32, best_idx=None, lambda_reg=0.3, scale_factor=1000, 
    expert_threshold=120_000, polygnn_model_path=None
):
    """
    Use property gradients to guide extrapolation, with checks for novelty and polymer validity.
    Now includes PolyGNN predictions for CO2 permeability.
    
    Args:
        polygnn_model_path: Path to pre-trained polyGNN model for CO2 permeability prediction
    """
    device = next(regression_model.parameters()).device

    # Load PolyGNN model if path is provided
    polygnn_ensemble = None
    polygnn_featurizer = None
    if polygnn_model_path:
        polygnn_ensemble, polygnn_featurizer, _ = load_polygnn_model(polygnn_model_path, device)
 

    # --- Freeze models to prevent parameter updates ---
    for param in regression_model.parameters():
        param.requires_grad = False
    regression_model.eval()

    for param in regression_expert_model.parameters():
        param.requires_grad = False
    regression_expert_model.eval()
    
    for param in generative_model.parameters():
        param.requires_grad = False
    generative_model.eval()

    # --- 1. Find the best starting embedding (batched) ---
    if best_idx is None:
        properties = []
        with torch.no_grad():
            for i in tqdm(range(0, len(embeddings), batch_size), desc="Computing initial properties"):
                batch = embeddings[i:i+batch_size]
                preds = regression_model.clf(batch)
                properties.append(preds[:, target_idx].cpu())
        properties = torch.cat(properties)
        best_idx = torch.argmax(properties)

    start_embedding = embeddings[best_idx].cuda().reshape(1, -1).requires_grad_(True)
    initial_embedding = start_embedding.clone().cuda()
    last_valid_embedding = start_embedding.clone().detach()

    # --- Store initial prediction for MAE calculation ---
    with torch.no_grad():
        initial_pred_scaled = pred_from_embeds(initial_embedding, regression_model)[:, target_idx]
        initial_pred_unscaled = initial_pred_scaled * torch.tensor(scaler.scale_, device=device) + torch.tensor(scaler.mean_, device=device)
        initial_prediction_value = initial_pred_unscaled.item()

    optimizer = torch.optim.Adam([start_embedding], lr=learning_rate)

    # --- Extract scaler attributes for PyTorch-based inverse transform ---
    scale = torch.tensor(scaler.scale_, device=device, dtype=torch.float32)
    mean = torch.tensor(scaler.mean_, device=device, dtype=torch.float32)
    
    # --- 2. Run gradient ascent with step-by-step checks ---
    predicting_model = regression_expert_model
    pred_unscaled = 0

    with torch.no_grad():
        pred = pred_from_embeds(start_embedding.cuda(), regression_model)
        sample_scaled = pred[:, target_idx]
        sample_unscaled = sample_scaled * scale + mean
        print(f'FIRST PRED: {sample_unscaled.detach().item()}') 

    for step in range(steps):
        if pred_unscaled >= expert_threshold:
            predicting_model = regression_expert_model
        else:
            predicting_model = regression_expert_model
    
        optimizer.zero_grad()

        pred_scaled = pred_from_embeds(start_embedding.cuda(), regression_model)[:, target_idx]
        pred_unscaled = pred_scaled * scale + mean
        property_loss = -pred_unscaled.mean()
        regularization_loss = torch.norm(start_embedding - initial_embedding, p=2)**2
        loss = property_loss + scale_factor * (lambda_reg * regularization_loss)
        
        loss.backward()
        optimizer.step()

        with torch.no_grad():
            start_embedding.clamp_(-20, 20)

        # --- VALIDATION BLOCK: Check molecule after each step ---
        with torch.no_grad():
            reconstructed_ids = generative_model.generate(start_embedding.cuda(), temperature=1.5)
            reconstructed_smiles = generative_model.tokenizer.decode(reconstructed_ids[0], skip_special_tokens=True)
            
            # Use the combined helper function for all checks
            is_valid_and_novel = is_novel_and_valid_polymer(reconstructed_smiles, training_smiles_set)
        
        print(f"Step {step+1}/{steps} | Value: {pred_unscaled.item():.4f} | SMILES: {reconstructed_smiles} | Novel & Valid Polymer: {is_valid_and_novel}")

        if is_valid_and_novel:
            # Tokenize the reconstructed SMILES
            recon_tokens = generative_model.tokenizer(
                reconstructed_smiles,
                max_length=512,
                padding='max_length',
                truncation=True,
                return_tensors='pt'
            ).to(device)
            
            # Get embedding from the reconstructed SMILES
            recon_embedding = generative_model.encoder(recon_tokens['input_ids'], recon_tokens['attention_mask'])
            
            CO2_scaled = pred_from_embeds(recon_embedding, predicting_model)[:, target_idx]
            CO2_unscaled = CO2_scaled * scale + mean
            
            print(f"  -> Reconstructed molecule CO2 permeability: {CO2_unscaled.item():.4f}")
            
            # --- NEW: PolyGNN CO2 permeability prediction ---
            if polygnn_ensemble and polygnn_featurizer:
                corrected_smiles = reconstructed_smiles.replace("I", "[*]")
                print(corrected_smiles)
                polygnn_pred = predict_co2_permeability_polygnn(
                    [corrected_smiles], 
                    polygnn_ensemble, 
                    polygnn_featurizer, 
                    polygnn_model_path, 
                    device
                )
                polygnn_pred = inverse_minmax(polygnn_pred)
                print(f"  -> PolyGNN CO2 permeability prediction: {polygnn_pred.item():.4f}")
                
                # Compare predictions
                pred_diff = abs(CO2_unscaled.item() - polygnn_pred.item())
                print(f"  -> Prediction difference (|Main - PolyGNN|): {pred_diff:.4f}")
                    

            
            # --- Calculate MAE between initial and reconstructed prediction ---
            mae_value = float(abs(CO2_unscaled + property_loss))
            print(f"  -> MAE between initial embedding prediction and current prediction: {mae_value:.4f}")

            # If it passes all checks, save this as the current best state
            last_valid_embedding = start_embedding.clone().detach()
        else:
            pass

    print(f'FINAL VALUE: {pred_unscaled.detach().item():.4f}')
    return last_valid_embedding


In [61]:
df['Smiles'][0]

'Ic1ccc(nc1)Cc1cccc(c1)Cc1ccc(cn1)N1C(=O)c2c(C1=O)cc(cc2)c1ccc2c(c1)C(=O)N(C2=O)I'

In [ ]:
result = gradient_based_extrapolation(
    generative_model=model,
    regression_model=regression_model,
    regression_expert_model=regression_model,
    embeddings=base_embeddings,
    scaler=scaler_co2,
    best_idx=best_idx,
    target_idx=-1,
    polygnn_model_path="polygnn/trained_models/solubility_and_permeability"
    
)

In [152]:
def get_min_max(real_values):
    """
    Derive the Min-Max‐scaler parameters directly from unscaled labels.

    Parameters
    ----------
    real_values : list | np.ndarray | torch.Tensor
        Iterable of ground-truth permeability values (original units).

    Returns
    -------
    tuple(float, float)
        (min_value, max_value) for the dataset.
    """
    arr = np.asarray(real_values, dtype=float)
    return float(arr.min()), float(arr.max())

mi, ma = get_min_max(df.sort_values(by=['CO2'], ascending=True).reset_index(drop=True)[:5_000_000]['CO2'])
mi, ma

(0.00419, 166.28537)

In [151]:
df.sort_values(by=['CO2'], ascending=False)

Unnamed: 0                                             Smiles  \
5117051     5117051  Ic1ccc(nc1)C(C(F)(F)F)(C(F)(F)F)c1ccc(nc1)C(C(...   
1654268     1654268  Ic1ccc(nc1)C(C(F)(F)F)(C(F)(F)F)c1ccc(cn1)C(C(...   
6692275     6692275  Ic1ccc(cn1)C(C(F)(F)F)(C(F)(F)F)c1ccc(cn1)C(C(...   
830270       830270  Ic1ccc(nc1)C(C(F)(F)F)(C(F)(F)F)c1ccc(nc1)C(C(...   
6692276     6692276  Ic1ccc(nc1)C(C(F)(F)F)(C(F)(F)F)c1ccc(nc1)C(C(...   
...             ...                                                ...   
10950         10950  Ic1cc(Oc2cc(Oc3cc(cc(c3)n3c(=O)c4c(c3=O)cc3c(c...   
5309014     5309014  Ic1cc(cc(c1)C(=O)O)C(=O)c1cc(cc(c1)C(=O)O)C(=O...   
2598418     2598418  Ic1cc(cc(c1)C(=O)O)C(=O)c1cc(cc(c1)C(=O)O)C(=O...   
746918       746918  Ic1cc(cc(c1)C(=O)O)C(=O)c1cc(cc(c1)C(=O)O)C(=O...   
2255           2255  Ic1cc(cc(c1)C(=O)O)C(=O)c1cc(cc(c1)C(=O)O)C(=O...   

             Tg         He          N2           O2        CH4           CO2  \
5117051  544.42  343.89398  3284.48720  18341.89400  528.13604  161379.46000   
1654268  544.42  343.89398  3284.48720  18341.89400  528.13604  161379.46000   
6692275  544.42  343.89398  3284.48720  18341.89400  528.13604  161379.46000   
830270   544.42  343.89398  3284.48720  18341.89400  528.13604  161379.46000   
6692276  544.42  343.89398  3284.48720  18341.89400  528.13604  161379.46000   
...         ...        ...         ...          ...        ...           ...   
10950    538.15    1.23546     0.00105      0.00404    0.00195       0.00785   
5309014  552.00    2.56385     0.00138      0.00777    0.00287       0.00772   
2598418  552.00    2.56385     0.00138      0.00777    0.00287       0.00772   
746918   552.00    2.56385     0.00138      0.00777    0.00287       0.00772   
2255     586.80    1.80544     0.00068      0.00330    0.00184       0.00419   

         synthesizable  
5117051          False  
1654268          False  
6692275          False  
830270           False  
6692276          False  
...                ...  
10950             True  
5309014          False  
2598418          False  
746918           False  
2255             False  

[6726950 rows x 9 columns]

In [76]:
import pandas as pd

In [77]:
df_sample = pd.read_csv('/home/jovyan/simson_training_bolgov/regression/polyGNN_combined_mols_.csv')[['SMILES', 'exp_perm_CO2__Barrer_mean']]
df_sample = df_sample.iloc[:100]
df_sample['SMILES'].to_list()

['[*]C(=O)c1ccc(N2C(=O)c3ccc(C(=O)c4ccc(C(=O)c5ccc(C(=O)c6ccc7c(c6)C(=O)N(c6ccc(C(=O)c8cccc([*])c8C)c(Cl)c6)C7=O)cn5)cn4)cc3C2=O)c(Cl)c1',
 '[*]c1ccc(Oc2cccc(Oc3ccc(N4C(=O)c5ccc(C(=O)c6ccc(C(=O)c7ccc8c(c7)C(=O)N([*])C8=O)cn6)cc5C4=O)cc3C)c2)c(C)c1',
 '[*]C(=O)c1ccc(N2C(=O)c3cccc(C(=O)c4ccc(Oc5ccc(C(=O)c6ccc7c(c6)C(=O)N(c6ccc(C(=O)c8ccc(C)c([*])c8)cc6Cl)C7=O)cc5)cc4)c3C2=O)cc1Cl',
 '[*]C(=O)c1cccc(C(=O)c2ccc3c(c2)C(=O)N(c2ccc(C(=O)c4ccc(C(=O)c5ccc(N6C(=O)c7ccc(C(=O)c8ccc([*])cc8)cc7C6=O)cc5Cl)cc4)c(Cl)c2)C3=O)c1',
 '[*]Cc1ccc(N2C(=O)c3ccc(Oc4ccc5c(c4)C(=O)N(c4ccc(Cc6cc(C)c([*])cc6C)c(Cl)c4)C5=O)cc3C2=O)cc1Cl',
 '[*]C(=O)c1ccc(C(=O)c2ccc3c(c2)C(=O)N(c2ccc(N4C(=O)c5ccc(C(=O)c6ccc([*])cc6)cc5C4=O)c(Cl)c2Cl)C3=O)cc1',
 '[*]Oc1ccc2c(c1)[nH]c1cc(Oc3cc(C(=O)O)cc(N4C(=O)c5ccc(Oc6ccc7ccc(Oc8cccc9c8C(=O)N(c8cc([*])cc(C(=O)O)c8)C9=O)cc7c6)cc5C4=O)c3)ccc12',
 '[*]c1ccc(C)c(N2C(=O)c3cccc(Oc4cccc(Sc5ccc6c(c5)C(=O)N([*])C6=O)c4)c3C2=O)c1',
 '[*]C(=O)c1ccc2c(c1)C(=O)N(c1ccc3c(c1)Cc1cc(N4C(=O)c5ccc(C(=O

In [78]:
df_sample

SMILES  \
0   [*]C(=O)c1ccc(N2C(=O)c3ccc(C(=O)c4ccc(C(=O)c5c...   
1   [*]c1ccc(Oc2cccc(Oc3ccc(N4C(=O)c5ccc(C(=O)c6cc...   
2   [*]C(=O)c1ccc(N2C(=O)c3cccc(C(=O)c4ccc(Oc5ccc(...   
3   [*]C(=O)c1cccc(C(=O)c2ccc3c(c2)C(=O)N(c2ccc(C(...   
4   [*]Cc1ccc(N2C(=O)c3ccc(Oc4ccc5c(c4)C(=O)N(c4cc...   
..                                                ...   
95  [*]C(=O)c1ccc2c(c1)C(=O)N(c1cccc3c(N4C(=O)c5cc...   
96  [*]C(=O)c1ccc2c(c1)C(=O)c1cc(C(=O)c3ccc(N4C(=O...   
97  [*]C(=O)c1cccc(N2C(=O)c3ccc(C(=O)c4ccc5c(c4)C(...   
98  [*]C(=O)c1ccc(C(=O)c2cccc3c2C(=O)N(c2ccc(C(=O)...   
99  [*]C(=O)c1cccc(Oc2ccc3c(c2)C(=O)N(c2ccc(C(=O)c...   

    exp_perm_CO2__Barrer_mean  
0                    0.669329  
1                    0.404411  
2                    0.785077  
3                    0.386811  
4                    0.733848  
..                        ...  
95                   1.072687  
96                   0.705203  
97                   0.285455  
98                   1.053971  
99                   0.651191  

[100 rows x 2 columns]

In [74]:
import math
def try_normalize(smiles):
    # функция выполняет перевод молекулы в формат rdkit и обратно. Это фильтрует некорректные молекулы и нормализует их, т.е. приводит к единому виду, чтобы затем можно было отфильтровать дубликаты молекул
    try:
        return Chem.MolToSmiles(Chem.MolFromSmiles(smiles))
    except Exception as e:
        # print(e)
        return None

polygnn_ensemble, polygnn_featurizer, path = load_polygnn_model("polygnn/trained_models/solubility_and_permeability", 'cuda')

def make_pred(smiles):
    corrected_smiles = [try_normalize(smile) for smile in smiles]
    corrected_smiles = [smile.replace("I", "[*]") for smile in smiles]
    
    #corrected_smiles = [smile.replace('*', 'I') for smile in corrected_smiles]
    y, mean, dev = predict_co2_permeability_polygnn(
        corrected_smiles, 
        polygnn_ensemble, 
        polygnn_featurizer, 
        path, 
        'cuda'
    )
    polygnn_preds = [10**(pred) for pred in mean]
    return polygnn_preds

df_sample = df.iloc[:100]
new_preds = make_pred(df_sample['Smiles'].to_list())

polyGNN model and configuration loaded successfully from pickle files.
The following properties will be modeled: ['exp_perm_CO2__Barrer']
Detected 100 data points for exp_perm_CO2__Barrer
[]


In [75]:
df_sample['new_preds'] = new_preds
df_sample.head(30)

Unnamed: 0                                             Smiles      Tg  \
0            0  Ic1ccc(nc1)Cc1cccc(c1)Cc1ccc(cn1)N1C(=O)c2c(C1...  494.84   
1            1  Ic1ccc(nc1)Cc1ccc2c(c1)cc(cc2)Cc1ccc(cn1)N1C(=...  508.26   
2            2  O=C1c2cc(ccc2C(=O)N1c1ccc(c(c1Cl)Cl)S(=O)(=O)c...  640.91   
3            3  Ic1cc(cc(c1)C(=O)O)C(=O)c1ccc2c(c1)ccc(c2)C(=O...  568.04   
4            4  Clc1cc(cc(c1)C(C(F)(F)F)(C(F)(F)F)c1c(C)cc(cc1...  548.10   
5            5  Cc1cc(Sc2ccc(nc2)Sc2cc(C)c(c(c2)C)I)cc(c1N1C(=...  501.82   
6            6  Cc1cc(Sc2ccc(cn2)Sc2cc(C)c(c(c2)C)I)cc(c1N1C(=...  501.82   
7            7  Clc1cc(ccc1C(=O)c1cc(ccc1C)C(=O)c1ccc(c(c1)Cl)...  529.64   
8            8  Ic1ccc(c(c1)Cl)C(=O)c1cc(ccc1C)C(=O)c1ccc(c(c1...  529.64   
9            9  Ic1ccc(c(c1)C)C(=O)c1cc2ccccc2cc1C(=O)c1ccc(cc...  556.31   
10          10  Ic1ccc(c(c1)Sc1cc(cc(c1)C(=O)O)Sc1cc(ccc1C)N1C...  470.24   
11          11  Cc1cc(cc(c1N1C(=O)c2c(C1=O)cc(cc2)c1ccc2c(c1)C...  575.93   
12          12  Ic1cc(C)c(c(c1)C)C(c1ccc2c(c1)[nH]c1c2ccc(c1)C...  537.39   
13          13  Ic1cc(Oc2ccc(cc2)C2(c3ccc(cc3)Oc3cc(cc(c3)N3C(...  556.56   
14          14  Ic1ccc(c(c1)Cl)Sc1ccc2c(c1)ccc(c2)Sc1ccc(c(c1)...  481.62   
15          15  Clc1cc(ccc1Sc1ccc2c(c1)ccc(c2)Sc1ccc(c(c1)Cl)I...  481.62   
16          16  Cc1cc(ccc1N1C(=O)c2c(C1=O)cccc2c1ccc2c(c1)C(=O...  596.88   
17          17  Ic1ccc(c(c1)C)C(c1ccc(cc1C)C(c1ccc(c(c1)C)N1C(...  467.07   
18          18  O=C1c2cccc(c2C(=O)N1c1ccc(c(c1)C)C(c1ccc(cc1C)...  467.07   
19          19  Cc1cc(c(cc1N1C(=O)c2c(C1=O)cc(cc2)c1ccc2c(c1)C...  668.95   
20          20  O=C1c2cc(ccc2c2c1cc(cc2)C(C(F)(F)F)(C(F)(F)F)c...  543.52   
21          21  Ic1ccc(cn1)C(c1cc(Cl)cc(c1)C(c1ccc(nc1)N1C(=O)...  508.98   
22          22  O=C1c2cccc(c2C(=O)N1c1cc(C)c(c(c1)C)S(=O)(=O)c...  628.48   
23          23  Ic1cc(C)c(c(c1)C)S(=O)(=O)c1ccc2c(c1)ccc(c2)S(...  628.48   
24          24  Ic1cc(Sc2cc(cc(c2)n2c(=O)c3c(c2=O)cc2c(c3)c(=O...  564.08   
25          25  Ic1ccc(cn1)C(=O)c1cc(C)c(c(c1)C)C(=O)c1ccc(cn1...  564.33   
26          26  Ic1ccc(nc1)C(=O)c1c(C)cc(cc1C)C(=O)c1ccc(nc1)n...  564.33   
27          27  Ic1cc(cc(c1)C(F)(F)F)C(=O)c1cc(C)c(cc1C)C(=O)c...  526.25   
28          28  Ic1ccc(cn1)S(=O)(=O)c1cc(C)c(c(c1)C)c1c(C)cc(c...  618.79   
29          29  Ic1ccc(c(c1)C(C(F)(F)F)(C(F)(F)F)c1cc(C)c(c(c1...  562.21   

           He        N2        O2      CH4        CO2  synthesizable  \
0     2.69524   4.75740  42.31847  1.64086  148.43644          False   
1     5.33815   2.97239  26.31118  0.86467   82.37635          False   
2    20.47515   0.06353   0.90498  0.06905    2.35993          False   
3     4.19692   0.00191   0.01134  0.00362    0.01418          False   
4   142.68327   0.87380   8.25409  2.52067   30.04739          False   
5    12.37968   1.68540  12.25254  1.03299   67.42722          False   
6    12.37968   1.68540  12.25254  1.03299   67.42722          False   
7    10.15046   0.02021   0.25611  0.13249    0.51867          False   
8    10.15046   0.02021   0.25611  0.13249    0.51867          False   
9    20.84491   0.05426   0.43648  0.06503    0.84243          False   
10    3.03201   0.02144   0.15934  0.02558    0.33708           True   
11  382.37918   4.71113  27.50459  4.06784  134.46742          False   
12  108.94866   1.07881   8.35180  1.67890   39.29826           True   
13    4.47037   0.04159   0.28007  0.03887    0.73329           True   
14    4.67411   0.01464   0.17388  0.05333    0.64280          False   
15    4.67411   0.01464   0.17388  0.05333    0.64280          False   
16   18.21650   0.09935   0.68089  0.12015    2.16558           True   
17   58.20149   0.51975   3.97824  0.68842   15.89978           True   
18   58.20149   0.51975   3.97824  0.68842   15.89978           True   
19   35.18491   0.13804   1.23473  0.07419    4.58177          False   
20  111.91630   1.33930   9.69874  0.95233   24.32080          False   
21   15.30320   7.27329  75.8624

In [40]:
df_sample['Smiles'].to_list()

['Ic1ccc(nc1)Cc1cccc(c1)Cc1ccc(cn1)N1C(=O)c2c(C1=O)cc(cc2)c1ccc2c(c1)C(=O)N(C2=O)I',
 'Ic1ccc(nc1)Cc1ccc2c(c1)cc(cc2)Cc1ccc(cn1)N1C(=O)c2c(C1=O)cccc2c1ccc2c(c1)C(=O)N(C2=O)I',
 'O=C1c2cc(ccc2C(=O)N1c1ccc(c(c1Cl)Cl)S(=O)(=O)c1ccc2c(c1)c1cc(ccc1C2(C)C)S(=O)(=O)c1ccc(c(c1Cl)Cl)I)c1ccc2c(c1)C(=O)N(C2=O)I',
 'Ic1cc(cc(c1)C(=O)O)C(=O)c1ccc2c(c1)ccc(c2)C(=O)c1cc(cc(c1)n1c(=O)c2c(c1=O)cc1c(c2)c(=O)n(c1=O)I)C(=O)O',
 'Clc1cc(cc(c1)C(C(F)(F)F)(C(F)(F)F)c1c(C)cc(cc1C)c1cc(C)c(c(c1)C)C(C(F)(F)F)(C(F)(F)F)c1cc(Cl)cc(c1)I)N1C(=O)c2c(C1=O)cccc2c1ccc2c(c1)C(=O)N(C2=O)I',
 'Cc1cc(Sc2ccc(nc2)Sc2cc(C)c(c(c2)C)I)cc(c1N1C(=O)c2c(C1=O)cccc2c1ccc2c(c1)C(=O)N(C2=O)I)C',
 'Cc1cc(Sc2ccc(cn2)Sc2cc(C)c(c(c2)C)I)cc(c1N1C(=O)c2c(C1=O)cccc2c1ccc2c(c1)C(=O)N(C2=O)I)C',
 'Clc1cc(ccc1C(=O)c1cc(ccc1C)C(=O)c1ccc(c(c1)Cl)I)N1C(=O)c2c(C1=O)cccc2c1ccc2c(c1)C(=O)N(C2=O)I',
 'Ic1ccc(c(c1)Cl)C(=O)c1cc(ccc1C)C(=O)c1ccc(c(c1)Cl)N1C(=O)c2c(C1=O)cccc2c1ccc2c(c1)C(=O)N(C2=O)I',
 'Ic1ccc(c(c1)C)C(=O)c1cc2ccccc2cc1C(=O)c1ccc(cc1C)N1C

In [32]:
df_sample['new_preds'] = new_preds
df_sample

Unnamed: 0                                             Smiles      Tg  \
0            0  Ic1ccc(nc1)Cc1cccc(c1)Cc1ccc(cn1)N1C(=O)c2c(C1...  494.84   
1            1  Ic1ccc(nc1)Cc1ccc2c(c1)cc(cc2)Cc1ccc(cn1)N1C(=...  508.26   
2            2  O=C1c2cc(ccc2C(=O)N1c1ccc(c(c1Cl)Cl)S(=O)(=O)c...  640.91   
3            3  Ic1cc(cc(c1)C(=O)O)C(=O)c1ccc2c(c1)ccc(c2)C(=O...  568.04   
4            4  Clc1cc(cc(c1)C(C(F)(F)F)(C(F)(F)F)c1c(C)cc(cc1...  548.10   
..         ...                                                ...     ...   
95          95  Ic1cc(cc(c1)C(=O)O)Oc1ccc(cc1C)Oc1cc(cc(c1)N1C...  528.86   
96          96  Ic1cc(Oc2ccc(c(c2)C)Oc2cc(cc(c2)N2C(=O)c3c(C2=...  528.86   
97          97  Cc1cc2c3cc(C)c(cc3S(=O)(=O)c2cc1Oc1ccc(c(c1)C)...  554.76   
98          98  Clc1c(ccc(c1Cl)N1C(=O)c2c(C1=O)cccc2c1ccc2c(c1...  575.95   
99          99  Ic1ccc(nc1)S(=O)(=O)c1ccc(c(c1Cl)Cl)S(=O)(=O)c...  639.66   

           He       N2        O2      CH4        CO2  synthesizable  \
0     2.69524  4.75740  42.31847  1.64086  148.43644          False   
1     5.33815  2.97239  26.31118  0.86467   82.37635          False   
2    20.47515  0.06353   0.90498  0.06905    2.35993          False   
3     4.19692  0.00191   0.01134  0.00362    0.01418          False   
4   142.68327  0.87380   8.25409  2.52067   30.04739          False   
..        ...      ...       ...      ...        ...            ...   
95    3.65897  0.00916   0.04655  0.01135    0.10014           True   
96    3.65897  0.00916   0.04655  0.01135    0.10014           True   
97   27.71933  0.37086   2.36356  0.10131    7.45523          False   
98    7.17213  0.01350   0.26675  0.21026    0.83210          False   
99    6.86828  2.80338  26.78062  0.40880  117.95785          False   

     new_preds  
0     1.036345  
1     2.058726  
2    21.385310  
3     0.802363  
4   132.455960  
..         ...  
95    1.777913  
96    1.777911  
97   10.918775  
98    2.465392  
99    4.053435  

[100 rows x 10 columns]

In [33]:
df_sample['Smiles'][0]

'Ic1ccc(nc1)Cc1cccc(c1)Cc1ccc(cn1)N1C(=O)c2c(C1=O)cc(cc2)c1ccc2c(c1)C(=O)N(C2=O)I'

In [67]:
CO2s = []
co2_preds = []
ch4_preds = []

robson_smiles = sample_df['Smiles'].tolist()

batch_size_robson = 128
for i in tqdm(range(0, len(robson_smiles), batch_size_robson), desc="Processing batches"):
    batch_end = min(i + batch_size_robson, len(robson_smiles))
    batch_smiles = robson_smiles[i:batch_end]
    
    # Step 3: Predict properties for both original and reconstructed
    # Original properties
    encoding = tokenizer(
                batch_smiles,
                max_length=256,
                padding='max_length',
                truncation=True,
                return_tensors='pt'
            )
            
    with torch.autocast(dtype=torch.float16, device_type='cuda'):
        with torch.no_grad():
            orig_predictions = regression_model(encoding['input_ids'].cuda(), encoding['attention_mask'].cuda())
    
    ch4_scaled = orig_predictions[:, -2].cpu().numpy().reshape(-1, 1)
    co2_scaled = orig_predictions[:, -1].cpu().numpy().reshape(-1, 1)

    ch4 = scaler_ch4.inverse_transform(ch4_scaled.astype(np.float64)).flatten()
    co2 = scaler_co2.inverse_transform(co2_scaled.astype(np.float64)).flatten()

    co2_preds.extend([float(pred) for pred in co2])
    ch4_preds.extend([float(pred) for pred in ch4])

df_robson['CO2_pred'] = co2_preds
df_robson['CH4_pred'] = ch4_preds


Processing batches: 100%|█████████████████████████| 8/8 [00:00<00:00, 18.36it/s]


In [70]:
if 'P_CO2/P_CH4' not in df_robson.columns:
    df_robson['P_CO2/P_CH4'] = df_robson['CO2_pred']/df_robson['CH4_pred']

In [71]:
k_2019 = 2.26e7
n_2019 = -2.401
k_2008 = 5_369_140
n_2008 = -2.636
k_1991 = 1_073_700
n_1991 = -2.6264

df_robson['upper_bound_Robeson'] = (df_robson['CO2_pred']/k_2019)**(1/n_2019)
df_robson['above_Robeson'] = df_robson['P_CO2/P_CH4'] > df_robson['upper_bound_Robeson']

df_robson['upper_bound_Robeson_2008'] = (df_robson['CO2_pred']/k_2008)**(1/n_2008)
df_robson['above_Robeson_2008'] = df_robson['P_CO2/P_CH4'] > df_robson['upper_bound_Robeson_2008']

df_robson['upper_bound_Robeson_1991'] = (df_robson['CO2_pred']/k_1991)**(1/n_1991)
df_robson['above_Robeson_1991'] = df_robson['P_CO2/P_CH4'] > df_robson['upper_bound_Robeson_1991']

In [72]:
num_bins = 20
x_points_on_Robeson2019_line = [  # референсные значения, использованные при подготовке обучающей выборки для первого этапа обучения
    0.4736211185063034,
    0.7707048833980547,
    1.2541375248783457,
    2.0408083109233783,
    3.3209265166816033,
    5.404012160362607,
    8.79373490580214,
    14.309696443824098,
    23.285602136958403,
    37.89173788621753,
    61.65972396131289,
    100.33642612016979,
    163.27349134558037,
    265.688484302277,
    432.3443451174293,
    703.5368252632127,
    1144.8376047731194,
    1862.9488809093987,
    3031.502912213795,
    4933.044594478952,
    8027.3480434650555]

log_bin_size = (np.log10(x_points_on_Robeson2019_line[1])-
                np.log10(x_points_on_Robeson2019_line[0]))/num_bins

print('(log) x_points_on_Robeson2019_line', [np.log10(xp) for xp in x_points_on_Robeson2019_line])
print('x_points_on_Robeson2019_line', x_points_on_Robeson2019_line)

(log) x_points_on_Robeson2019_line [np.float64(-0.3245689409002736), np.float64(-0.11311188919602205), np.float64(0.0983451625082295), np.float64(0.30980221421248105), np.float64(0.5212592659167326), np.float64(0.7327163176209841), np.float64(0.9441733693252357), np.float64(1.1556304210294872), np.float64(1.3670874727337388), np.float64(1.5785445244379903), np.float64(1.7900015761422419), np.float64(2.0014586278464934), np.float64(2.212915679550745), np.float64(2.424372731254997), np.float64(2.6358297829592483), np.float64(2.8472868346634996), np.float64(3.0587438863677514), np.float64(3.270200938072003), np.float64(3.4816579897762545), np.float64(3.693115041480506), np.float64(3.9045720931847576)]
x_points_on_Robeson2019_line [0.4736211185063034, 0.7707048833980547, 1.2541375248783457, 2.0408083109233783, 3.3209265166816033, 5.404012160362607, 8.79373490580214, 14.309696443824098, 23.285602136958403, 37.89173788621753, 61.65972396131289, 100.33642612016979, 163.27349134558037, 265.688

In [73]:
# определение бинов Робсона, для последующей отрисовки матрицы путанности

def calculate_bin(row, x_col, y_col):
    x_point = row[x_col]
    y_point = row[y_col]
    slope = (1/n_2019)
    
    bin_for_point = 1
    for x_line in x_points_on_Robeson2019_line[1:]:
        y_Robeson = (x_line/k_2019)**(1/n_2019)  # upper_bound_Robeson_2019
        y_bin = 10**(-1/slope * np.log10(x_point/x_line) + np.log10(y_Robeson))
        if y_point > y_bin:
            break
        bin_for_point += 1
    return bin_for_point

df_robson['Robeson_bin'] = df_robson.apply(calculate_bin,
                                           x_col='CO2_pred',
                                           y_col='P_CO2/P_CH4',
                                           axis=1)

/tmp/ipykernel_265640/2901639124.py:11: RuntimeWarning:

invalid value encountered in log10



In [74]:
import ipywidgets
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
import plotly.io as pio

pio.renderers.default = "notebook"  # fixes duplicate plotly plots problem

In [77]:
df

Unnamed: 0                                             Smiles  \
0                 0  Ic1ccc(nc1)Cc1cccc(c1)Cc1ccc(cn1)N1C(=O)c2c(C1...   
1                 1  Ic1ccc(nc1)Cc1ccc2c(c1)cc(cc2)Cc1ccc(cn1)N1C(=...   
2                 2  O=C1c2cc(ccc2C(=O)N1c1ccc(c(c1Cl)Cl)S(=O)(=O)c...   
3                 3  Ic1cc(cc(c1)C(=O)O)C(=O)c1ccc2c(c1)ccc(c2)C(=O...   
4                 4  Clc1cc(cc(c1)C(C(F)(F)F)(C(F)(F)F)c1c(C)cc(cc1...   
...             ...                                                ...   
6726945     6726945  Ic1cccc(c1)Cc1cc(C)c(c(c1)C)c1c(C)cc(cc1C)Cc1c...   
6726946     6726946  Ic1ccc(nc1)Cc1ccc2c(c1)c1cc(ccc1C2(C)C)Cc1ccc(...   
6726947     6726947  Ic1ccc(cn1)S(=O)(=O)c1ccc(nc1)N1C(=O)c2c(C1=O)...   
6726948     6726948  Ic1ccc(c(c1)C)Oc1ccc2c(c1)Cc1c2ccc(c1)Oc1ccc(c...   
6726949     6726949  Ic1cc(Sc2ccc3c(c2)cc(cc3)Sc2cc(cc(c2)C(F)(F)F)...   

             Tg         He        N2         O2      CH4        CO2  \
0        494.84    2.69524   4.75740   42.31847  1.64086  148.43644   
1        508.26    5.33815   2.97239   26.31118  0.86467   82.37635   
2        640.91   20.47515   0.06353    0.90498  0.06905    2.35993   
3        568.04    4.19692   0.00191    0.01134  0.00362    0.01418   
4        548.10  142.68327   0.87380    8.25409  2.52067   30.04739   
...         ...        ...       ...        ...      ...        ...   
6726945  516.27   13.32967   0.11907    1.10144  0.16907    2.63642   
6726946  510.72    8.96454   7.92257   72.92929  2.17324  247.14446   
6726947  610.24    4.90758  20.24364  121.24494  1.01011  650.18364   
6726948  510.90   12.40907   0.19307    1.41335  0.11728    4.00573   
6726949  462.31   14.96342   0.13916    1.05252  0.09298    2.54411   

         synthesizable  
0                False  
1                False  
2                False  
3                False  
4                False  
...                ...  
6726945          False  
6726946          False  
6726947          False  
6726948           True  
6726949          False  

[6726950 rows x 9 columns]

In [76]:
# отрисовка троек молекул (2 разгонных + 1 сгенерированная) на диаграмме Робсона

# new_pi_df_unique = new_pi_df.drop_duplicates(['smiles_start'])
sub_df_preds = df_robson.sample(frac=1, random_state=1010)


def plot_with_controls(num_points=1):


  sub_df_preds_plotted = sub_df_preds.iloc[:num_points]

  x_stuff = 'CO2'
  y_stuff = 'P_CO2/P_CH4'

  
  log_scale = True
  fig = px.scatter(sub_df_preds_plotted, x=x_stuff, y=y_stuff, log_x=log_scale, log_y=log_scale, 
                   color_discrete_sequence=['red'],
    )

     
  fig2 = px.line(sub_df_preds.iloc[:1000],
                 x='CO2_pred', y='upper_bound_Robeson', labels='Robeson_2019')
  fig2.update_traces(line_color='red', line_width=1)
  fig3 = px.line(sub_df_preds.iloc[:1000],
                 x='CO2_pred', y='upper_bound_Robeson_2008', labels='Robeson_2008')
  fig3.update_traces(line_color='green', line_width=1)
  fig4 = px.line(sub_df_preds.iloc[:1000],
                 x='CO2_pred', y='upper_bound_Robeson_1991', labels='Robeson_1991')
  fig4.update_traces(line_color='blue', line_width=1)
  fig = go.Figure(data=fig.data + fig2.data + fig3.data + fig4.data, layout = fig.layout)
  fig.update_layout(fig2.layout)

  fig.update_layout(width=1100, height=550, margin=dict(l=40, r=40, t=10, b=10),)

  list_of_all_arrows = []
  
  
          
  fig.show()


num_points_slider = ipywidgets.IntSlider(
    # value=len(sub_df_preds),
    value=10,
    # min=1000,
    min=10,
    # max=len(sub_df_preds),
    max=min(len(sub_df_preds),1000),
    step=10,
    description='Num points',
    disabled=False,
    continuous_update=False,
    orientation='horizontal',
    readout=True,
    readout_format='d'
)



output = ipywidgets.interactive_output(plot_with_controls,
                                       {
                                        'num_points': num_points_slider,
                                        })
display(num_points_slider, output)

IntSlider(value=10, continuous_update=False, description='Num points', max=1000, min=10, step=10)

Output()

In [ ]:

reconstructed_ids = model.generate(best_embedding)
reconstructed_smiles = [tokenizer.decode(seq, skip_special_tokens=True) for seq in reconstructed_ids]
mol_gen = Chem.MolFromSmiles(reconstructed_smiles[0])

print(reconstructed_smiles[0])

if mol_gen is not None:
    print('Valid')
else:
    print('Skill issue')

In [ ]:
def comprehensive_generation(model, tokenizer, val_df, base_embeddings):
    """Generate molecules with different enhancement levels"""
    
    all_results = []
    extrapolation_factors = [factor / 1000 for factor in range(0, 100, 10)]
    print(extrapolation_factors)
    for factor in extrapolation_factors:
        co2_results = generate_gradient(
            model, tokenizer, base_embeddings, val_df, 'CO2', extrapolation_factor=factor)

        all_results.extend(co2_results)# + ch4_results + dual_results)
    
    return all_results

# Run comprehensive generation
all_generated_molecules = comprehensive_generation(model, tokenizer, df, base_embeddings)

In [ ]:
def predict_molecule_properties(smiles_list, regression_model, tokenizer, scaler_ch4, scaler_co2, 
                               batch_size=32, max_length=512, 
                               baseline_ch4=None, baseline_co2=None):
    """
    Predict CO2 and CH4 permeability properties for a list of SMILES

    Returns:
        ch4_predictions: Array of CH4 permeability predictions
        CO2ictions: Array of CO2 permeability predictions
        molecules_exceeding_baselines: List of dicts for molecules exceeding baselines
    """
    device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
    regression_model.to(device)
    regression_model.eval()

    all_predictions = []
    with torch.no_grad():
        for i in range(0, len(smiles_list), batch_size):
            batch_smiles = smiles_list[i:i+batch_size]

            tokens = tokenizer(
                batch_smiles,
                max_length=max_length,
                truncation=True,
                padding='max_length',
                return_tensors='pt'
            )
            input_ids = tokens['input_ids'].to(device)
            attention_mask = tokens['attention_mask'].to(device)

            predictions = regression_model(input_ids, attention_mask)
            all_predictions.append(predictions.cpu().numpy())

    all_predictions = np.vstack(all_predictions)
    ch4_scaled = all_predictions[:, -2].reshape(-1, 1)
    co2_scaled = all_predictions[:, -1].reshape(-1, 1)

    ch4_predictions = scaler_ch4.inverse_transform(ch4_scaled).flatten()
    CO2ictions = scaler_co2.inverse_transform(co2_scaled).flatten()

    # Use provided baselines or max in predictions
    if baseline_ch4 is None:
        baseline_ch4 = ch4_predictions.max()
    if baseline_co2 is None:
        baseline_co2 = CO2ictions.max()

    molecules_exceeding_baselines = []
    for idx, (smiles, ch4_pred, CO2) in enumerate(zip(smiles_list, ch4_predictions, CO2ictions)):
        exceeds_ch4 = ch4_pred > baseline_ch4
        exceeds_co2 = CO2 > baseline_co2
        if exceeds_ch4 or exceeds_co2:
            molecules_exceeding_baselines.append({
                "index": idx,
                "smiles": smiles,
                "predicted_CH4": ch4_pred,
                "predicted_CO2": CO2,
                "exceeds_CH4": exceeds_ch4,
                "exceeds_CO2": exceeds_co2
            })

    return ch4_predictions, CO2ictions, molecules_exceeding_baselines


def analyze_generated_molecules_with_properties(generated_molecules, regression_model, tokenizer, 
                                               scaler_ch4, scaler_co2, val_df):
    """
    Analyze generated molecules and predict their actual properties
    
    Args:
        generated_molecules: List of generated molecule dictionaries
        regression_model: Trained regression model
        tokenizer: SMILES tokenizer
        scaler_ch4, scaler_co2: Property scalers
        val_df: Validation dataframe for baseline comparison
    
    Returns:
        enhanced_results: DataFrame with predicted properties
    """
    
    # Extract SMILES from generated molecules
    generated_smiles = []
    for mol in generated_molecules:
        if mol['is_valid']:  # Only predict for valid molecules
            generated_smiles.append(mol['generated_smiles'])
    
    if not generated_smiles:
        print("No valid molecules to analyze!")
        return None
    
    print(f"Predicting properties for {len(generated_smiles)} valid generated molecules...")
    
    # Predict properties
    pred_ch4, pred_co2, molecules_exceeding_baselines = predict_molecule_properties(
        generated_smiles, regression_model, tokenizer, scaler_ch4, scaler_co2,
        baseline_ch4=val_df['CH4'].max(),
        baseline_co2=val_df['CO2'].max()
    )
    
    # Create results dataframe
    results_data = []
    pred_idx = 0
    
    for mol in generated_molecules:
        if mol['is_valid']:
            results_data.append({
                'generated_smiles': mol['generated_smiles'],
                'target_property': mol['target_property'],
                'extrapolation_factor': mol['extrapolation_factor'],
                'predicted_CH4': pred_ch4[pred_idx],
                'predicted_CO2': pred_co2[pred_idx],
                'is_valid': mol['is_valid']
            })
            pred_idx += 1
        else:
            # Include invalid molecules with NaN predictions
            results_data.append({
                'generated_smiles': mol['generated_smiles'],
                'target_property': mol['target_property'],
                'extrapolation_factor': mol['extrapolation_factor'],
                'predicted_CH4': np.nan,
                'predicted_CO2': np.nan,
                'is_valid': mol['is_valid']
            })
    
    results_df = pd.DataFrame(results_data)
    
    # Calculate baseline statistics from validation set
    baseline_ch4_mean = val_df['CH4'].mean()
    baseline_ch4_max = val_df['CH4'].max()
    baseline_co2_mean = val_df['CO2'].mean()
    baseline_co2_max = val_df['CO2'].max()
    
    # Calculate enhancement statistics for valid molecules only
    valid_results = results_df[results_df['is_valid']].copy()
    
    if len(valid_results) > 0:
        print(f"\n{'='*80}")
        print(f"INDIVIDUAL MOLECULE PROPERTIES")
        print(f"{'='*80}")
        
        # Display properties for each individual molecule
        for idx, (_, mol) in enumerate(valid_results.iterrows(), 1):
            ch4_vs_baseline = (mol['predicted_CH4'] / baseline_ch4_max - 1) * 100
            co2_vs_baseline = (mol['predicted_CO2'] / baseline_co2_max - 1) * 100
            
            print(f"  SMILES: {mol['generated_smiles']}")
            print(f"  Target: {mol['target_property']} (factor: {mol['extrapolation_factor']})")
            print(f"  CH₄ Permeability: {mol['predicted_CH4']:.4f} ({ch4_vs_baseline:+.1f}% vs baseline max)")
            print(f"  CO₂ Permeability: {mol['predicted_CO2']:.4f} ({co2_vs_baseline:+.1f}% vs baseline max)")
            
            # Enhancement indicators
            enhancement_flags = []
            if mol['predicted_CH4'] > baseline_ch4_max:
                enhancement_flags.append("CH₄↑")
            if mol['predicted_CO2'] > baseline_co2_max:
                enhancement_flags.append("CO₂↑")
            if enhancement_flags:
                print(f"  Enhancements: {', '.join(enhancement_flags)}")
            
            print("-" * 70)
  
        print(f"Baseline Dataset Statistics:")
        print(f"  CH4 - Mean: {baseline_ch4_mean:.4f}, Max: {baseline_ch4_max:.4f}")
        print(f"  CO2 - Mean: {baseline_co2_mean:.4f}, Max: {baseline_co2_max:.4f}")
        
        print(f"\nGenerated Molecules Statistics:")
        print(f"  CH4 - Mean: {valid_results['predicted_CH4'].mean():.4f}, Max: {valid_results['predicted_CH4'].max():.4f}")
        print(f"  CO2 - Mean: {valid_results['predicted_CO2'].mean():.4f}, Max: {valid_results['predicted_CO2'].max():.4f}")
        
        # Check for improvements
        ch4_improvements = valid_results['predicted_CH4'] > baseline_ch4_max
        co2_improvements = valid_results['predicted_CO2'] > baseline_co2_max
        print(f"\nEnhancement Analysis:")
        print(f"  Molecules exceeding baseline CH4 max: {ch4_improvements.sum()}/{len(valid_results)} ({ch4_improvements.mean()*100:.1f}%)")
        print(f"  Molecules exceeding baseline CO2 max: {co2_improvements.sum()}/{len(valid_results)} ({co2_improvements.mean()*100:.1f}%)")
        # Enhancement by target property
        property_analysis = valid_results.groupby('target_property').agg({
            'predicted_CH4': ['mean', 'max', 'count'],
            'predicted_CO2': ['mean', 'max', 'count']
        }).round(4)
        
        print(f"\nProperty Enhancement by Generation Target:")
        
        # Enhancement by extrapolation factor
        factor_analysis = valid_results.groupby('extrapolation_factor').agg({
            'predicted_CH4': ['mean', 'max'],
            'predicted_CO2': ['mean', 'max']
        }).round(4)
        
        print(f"\nProperty Enhancement by Extrapolation Factor:")
        print("\nMolecules that exceed baselines:")
        for mol in molecules_exceeding_baselines:
            print(f"SMILES: {mol['smiles']}")
            print(f"  CH₄ Predicted: {mol['predicted_CH4']:.4f} (Exceeds baseline: {mol['exceeds_CH4']})")
            print(f"  CO₂ Predicted: {mol['predicted_CO2']:.4f} (Exceeds baseline: {mol['exceeds_CO2']})\n")

    
    
    else:
        print("No valid molecules generated for property prediction!")
    
    return results_df, molecules_exceeding_baselines


In [ ]:
results_df, molecules_exceeding_baselines = analyze_generated_molecules_with_properties(
    all_generated_molecules, regression_model, tokenizer, scaler_ch4, scaler_co2, df
)

In [ ]:
exceeding_mols = []
for mol_info in molecules_exceeding_baselines:
    if mol_info['exceeds_CH4'] and mol_info['exceeds_CO2']:
        exceeding_mols.append(mol_info['smiles'])

exceeding_mols

In [ ]:
smiles_generated_col = 'smiles'
gen_df = pd.DataFrame({smiles_generated_col: exceeding_mols})

In [ ]:
def split_dot(smiles):
    if '.' in smiles:
        parts = smiles.split('.')
        # выбираем наиболее длинную отдельную часть молекулы в качестве самой молекулы
        smiles = sorted(parts, key=lambda x:len(x), reverse=True)[0]
    return smiles

partial_mols_count = sum(gen_df[smiles_generated_col].str.contains('.', regex=False))
print(f'{partial_mols_count} partial mols fixed')
if partial_mols_count > 0:
    gen_df[smiles_generated_col] = gen_df[smiles_generated_col].transform(split_dot)

In [ ]:
def try_normalize(smiles):
    # функция выполняет перевод молекулы в формат rdkit и обратно. Это фильтрует некорректные молекулы и нормализует их, т.е. приводит к единому виду, чтобы затем можно было отфильтровать дубликаты молекул
    try:
        return Chem.MolToSmiles(Chem.MolFromSmiles(smiles))
    except Exception as e:
        # print(e)
        return None

In [ ]:
symbols = ['*', '[*]', 'I']
contain_counts = {}
for symbol in symbols:
    contain_counts[symbol] = gen_df[smiles_generated_col].apply(lambda smiles: symbol in smiles).sum()
    print(f'contain {symbol}: {contain_counts[symbol]} mols')

most_frequent_symbol = max(contain_counts, key=contain_counts.get)
assert most_frequent_symbol == 'I'  # else think about it

In [ ]:
gen_df[smiles_generated_col] = gen_df[smiles_generated_col].transform(lambda x: x.replace('[*]', 'I'))
gen_df[smiles_generated_col] = gen_df[smiles_generated_col].transform(lambda x: x.replace('*', 'I'))

In [ ]:
smiles_normalized_col = 'SMILES_normalized'

gen_df[smiles_normalized_col] = gen_df[smiles_generated_col].apply(try_normalize)

n_before = len(gen_df)
gen_df = gen_df.loc[~gen_df[smiles_normalized_col].isnull()]
n_after = len(gen_df)

print(f'deleted: {n_before-n_after} incorrect mols'
      f' (before: {n_before} mols, after: {n_after} mols)')

In [ ]:
temp_smiles_col = smiles_normalized_col+'2'
gen_df[temp_smiles_col] = gen_df[smiles_normalized_col].apply(try_normalize)

n_before = len(gen_df)
gen_df = gen_df.loc[~gen_df[temp_smiles_col].isnull()]
n_after = len(gen_df)

gen_df = gen_df.drop(columns=[temp_smiles_col])

print(f'deleted: {n_before-n_after} incorrect mols'
      f' (before: {n_before} mols, after: {n_after} mols)')

In [ ]:
n_before = len(gen_df)
gen_df = gen_df.drop_duplicates(subset=[smiles_normalized_col])
n_after = len(gen_df)

print(f'deleted: {n_before-n_after} duplicates'
      f' (before: {n_before} mols, after: {n_after} mols)')

In [ ]:
def filter_two_endpoints(smiles):
    return smiles if smiles.count('I') == 2 else None


gen_df[smiles_generated_col] = gen_df[smiles_generated_col].apply(filter_two_endpoints)

n_before = len(gen_df)
gen_df = gen_df.loc[~gen_df[smiles_generated_col].isnull()]
n_after = len(gen_df)

print(f'deleted: {n_before-n_after} incorrect mols'
      f' (before: {n_before} mols, after: {n_after} mols)')

In [ ]:
def filter_matching_endpoint_bonds(smiles):
    # фильтрация на предмет того, что типы связей у эндпоинтов должны быть одинаковы
    try:
        mol = Chem.MolFromSmiles(smiles.replace('I', '[*]'))
        inds = tuple(mol.GetSubstructMatches(Chem.MolFromSmarts("[#0]~*")))
        inds = tuple(zip(*inds))
        star_inds = list(inds[0])
        connector_inds = list(inds[1])
        b1_type = mol.GetBondBetweenAtoms(star_inds[0], connector_inds[0]).GetBondType()
        b2_type = mol.GetBondBetweenAtoms(star_inds[1], connector_inds[1]).GetBondType()
        if b1_type != b2_type:
            return None
        else:
            return smiles
    except:
        return None
gen_df[smiles_generated_col] = gen_df[smiles_generated_col].apply(filter_matching_endpoint_bonds)

n_before = len(gen_df)
gen_df = gen_df.loc[~gen_df[smiles_generated_col].isnull()]
n_after = len(gen_df)

print(f'deleted: {n_before-n_after} incorrect mols'
      f' (before: {n_before} mols, after: {n_after} mols)')

In [ ]:
molecules_exceeding_baselines

In [ ]:
gen_df = gen_df.reset_index(drop=True)
gen_df

In [ ]:
exceeding_mols_co2 = []
exceeding_mols_ch4 = []

for mol in gen_df['smiles']:
    for candidat_mol_info in molecules_exceeding_baselines:
        if mol == candidat_mol_info['smiles']:
            exceeding_mols_co2.append(float(candidat_mol_info['predicted_CO2']))
            exceeding_mols_ch4.append(float(candidat_mol_info['predicted_CH4']))
            break

exceeding_mols_co2, exceeding_mols_ch4

In [ ]:
gen_df['smiles'].to_list()

In [ ]:
gen_df['predicted_CO2'] = exceeding_mols_co2
gen_df['predicted_CH4'] = exceeding_mols_ch4
gen_df

In [ ]:
final_output = '/home/jovyan/simson_training_bolgov/regression/exceeding_mols.csv'
gen_df.to_csv(final_output, index=False)

In [ ]:
df_robson = gen_df
df_robson['P_CO2/P_CH4'] = gen_df['predicted_CO2']/gen_df['predicted_CH4']

In [ ]:
t = df_robson['smiles'][0]
df_robson.iloc[0]

In [ ]:
df[df['Smiles'] == t]

In [ ]:
df_robson['in_synth_DB'] = df_robson['smiles'].isin(df['Smiles'])
df_robson